In [ ]:
# Following need terminal access or silent install:
# !conda update -y -n base -c conda-forge conda
# !conda install -y tiktoken
# !conda install -y bitsandbytes
# !conda install -y pytorch torchvision torchaudio pytorch-cuda=12.1 -c pytorch -c nvidia

# To install a pre-release version of PyTorch.
# - https://discuss.pytorch.org/t/pytorch-for-cuda-12/169447/40?page=2
# - https://stackoverflow.com/questions/5189199/bypass-confirmation-prompt-for-pip-uninstall
# !python3 -m -y pip uninstall torch torchaudio torchvision torchviz
# !python3 -m pip install --upgrade --pre torch torchvision torchaudio --index-url https://download.pytorch.org/whl/nightly/cu121

# !python3 -m pip install torch torchvision torchaudio
# !python3 -m pip install bitsandbytes
# !python3 -m pip install tiktoken

# !python3 -m pip freeze > requirements.txt
# !python3 -m pip install -r requirements.txt

In [ ]:
# Test installation:
import torch
print(torch.__version__)
!python3 -m bitsandbytes

In [ ]:
import os
import re
import math
import time
import inspect
import random
import pickle
import platform

from datetime import datetime

import json

from abc import ABC, abstractmethod

from collections import Counter, defaultdict
from typing import List, Union, Dict, Any, Optional

from dataclasses import dataclass

import requests

import numpy as np

import torch

import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch import Tensor
from torch.cuda.amp import GradScaler, autocast
from torch.utils.data import Dataset, DataLoader, random_split

import matplotlib.pyplot as plt

import tiktoken
from tiktoken import get_encoding

from tqdm import tqdm

from IPython import display
import gc

In [ ]:
# !pip install bitsandbytes -U
# https://nn.labml.ai/neox/utils/llm_int8.htm

try:
    from bitsandbytes.nn import Linear8bitLt, Int8Params
except ImportError:
    raise ImportError('''Please install `bitsandbytes` with `pip install bitsandbytes -U`''')

import torch
from torch import nn

def make_llm_int8_linear(linear_module: nn.Linear, device: torch.device, threshold: float = 6.0):
    """
    Transform a nn.Linear layer to LLM.int8() linear layer
    linear_module is the nn.Linear layer to transform
    device is the device of the model
    threshold is the threshold α to use for outlier detection
    """
    
    assert isinstance(linear_module, nn.Linear)

    # Create an empty Linear8bitLt module.
    int8_lin = Linear8bitLt(
        linear_module.in_features,
        linear_module.out_features,
        linear_module.bias is not None,
        has_fp16_weights=False,
        threshold=threshold,
    )

    # Quantize the weights.
    int8_lin._parameters['weight'] = Int8Params(
        linear_module.weight.data.cpu(),
        requires_grad=False,
        has_fp16_weights=False).to(device)

    # Set the bias in float16 space.
    if linear_module.bias is not None:
        int8_lin._parameters['bias'] = nn.Parameter(
            linear_module.bias.data,
            requires_grad=False
        )

    return int8_lin

In [ ]:

class BaseTokenizer(ABC):
    def __init__(self):
        """
        Base tokenizer to define the interface for all tokenizers.

        Attributes:
            token_to_item (Dict[int, str]): A mapping of token index to token.
            item_to_token (Dict[str, int]): A mapping of token to token index.
            current_index (int): The current index to keep track of token additions.
        """
        self.token_to_item: Dict[int, str] = {0: ""}
        self.item_to_token: Dict[str, int] = {"": 0}
        self.current_index: int = 1

    @abstractmethod
    def train(self, document: str) -> None:
        """
        Abstract method for training the tokenizer.

        Args:
            document (str): The training document used to build the vocabulary.
        """
        pass

    @abstractmethod
    def encode(self, text: str) -> List[int]:
        """
        Abstract method for encoding a text into tokens.

        Args:
            text (str): The input text to be encoded.

        Returns:
            List[int]: The list of encoded tokens as integers.
        """
        pass

    @abstractmethod
    def decode(self, tokens: List[int]) -> str:
        """
        Abstract method for decoding tokens back into text.

        Args:
            tokens (List[int]): The list of tokens to be decoded.

        Returns:
            str: The decoded text.
        """
        pass

    @abstractmethod
    def vocab_size(self) -> int:
        """
        Abstract method to get the vocabulary size of the tokenizer.

        Returns:
            int: The vocabulary size.
        """
        pass


class SimpleTokenizer(BaseTokenizer):
    def __init__(self, char_level: bool = True):
        """
        Simple tokenizer class that extends the base tokenizer.

        Args:
            char_level (bool, optional): Determines whether to tokenize at the character level.
                Defaults to True.
        """
        super().__init__()
        self.char_level: bool = char_level

    def train(self, document: str) -> None:
        """
        Train the simple tokenizer by adding unique characters and words to the vocabulary.

        Args:
            document (str): The training document used to build the vocabulary.
        """
        for character in set(document):
            if character not in self.item_to_token:
                self.item_to_token[character] = self.current_index
                self.token_to_item[self.current_index] = character
                self.current_index += 1

        if not self.char_level:
            words = re.findall(r'\S+|\s+', document)
            for word in set(words):
                if word not in self.item_to_token:
                    self.item_to_token[word] = self.current_index
                    self.token_to_item[self.current_index] = word
                    self.current_index += 1

    def encode(self, text: str) -> List[int]:
        """
        Encode text by converting it into a sequence of tokens.

        Args:
            text (str): The input text to be encoded.

        Returns:
            List[int]: The list of encoded tokens as integers.
        """
        tokens = []
        words = re.findall(r'\S+|\s+', text)
        for word in words:
            token = self.item_to_token.get(word, None)
            if token is not None:
                tokens.append(token)
            else:
                tokens.extend(self.item_to_token.get(char, self.item_to_token[""]) for char in word)
        return tokens

    def decode(self, tokens: List[int]) -> str:
        """
        Decode tokens back into the original text.

        Args:
            tokens (List[int]): The list of tokens to be decoded.

        Returns:
            str: The decoded text.
        """
        return "".join(self.token_to_item.get(token, "") for token in tokens)

    def vocab_size(self) -> int:
        """
        Get the vocabulary size of the simple tokenizer.

        Returns:
            int: The vocabulary size.
        """
        return len(self.item_to_token)


class TikTokenizer(BaseTokenizer):
    def __init__(self, encoding: str = "cl100k_base"):
        """
        TikTokenizer class, another tokenizer based on some encoding.

        Args:
            encoding (str, optional): The type of encoding to use. Defaults to "cl100k_base".
        """

        """
        cl100k_base = tiktoken.get_encoding("cl100k_base")
        
        # In production, load the arguments directly instead of accessing private attributes
        # See openai_public.py for examples of arguments for specific encodings
        enc = tiktoken.Encoding(
            # If you're changing the set of special tokens, make sure to use a different name
            # It should be clear from the name what behaviour to expect.
            name="cl100k_im",
            pat_str=cl100k_base._pat_str,
            mergeable_ranks=cl100k_base._mergeable_ranks,
            special_tokens={
                **cl100k_base._special_tokens,
                "<|im_start|>": 100264,
                "<|im_end|>": 100265,
            }
        )
        
        # GPT3.5 (cl100k_base) Specific.
        # {
        #     '<|endoftext|>': 100257,
        #     '<|fim_prefix|>': 100258,
        #     '<|fim_middle|>': 100259,
        #     '<|fim_suffix|>': 100260,
        #     '<|endofprompt|>': 100276
        # }
        """
        
        super().__init__()

        if encoding == "cl100k_base":
            enc_base = get_encoding(encoding)

            self.enc = tiktoken.Encoding(
                name=f"{encoding}_prk",
                pat_str=enc_base._pat_str,
                mergeable_ranks=enc_base._mergeable_ranks,
                special_tokens={
                    **enc_base._special_tokens,
                    "<|padding|>": enc_base.max_token_value + 1,
                    "\n\nSystem: ": enc_base.max_token_value + 2,
                    "\n\nHuman: ": enc_base.max_token_value + 3,
                    "\n\nAssistant: ": enc_base.max_token_value + 4,
                }
            )
        else:
            enc_base = tiktoken.get_encoding(encoding)
            
            self.enc = tiktoken.Encoding(
                name=f"{encoding}_prk",
                pat_str=enc_base._pat_str,
                mergeable_ranks=enc_base._mergeable_ranks,
                special_tokens={
                    **enc_base._special_tokens,
                    "<|endofprompt|>": enc_base.max_token_value + 1,
                    "<|padding|>": enc_base.max_token_value + 2,
                    "\n\nSystem: ": enc_base.max_token_value + 3,
                    "\n\nHuman: ": enc_base.max_token_value + 4,
                    "\n\nAssistant: ": enc_base.max_token_value + 5,
                }
            )
        
        self.eot_text: str = "<|endoftext|>"      # End-of-text special token.
        self.eop_text: str = "<|endofprompt|>"    # End-of-prompt special token.
        self.pad_text: str = "<|padding|>"        # <|padding|>` instead...

        self.sys_text: str = "\n\nSystem: "
        self.usr_text: str = "\n\nHuman: "
        self.bot_text: str = "\n\nAssistant: "
        
        self.eot_token: int = self.enc.encode(self.eot_text, allowed_special={self.eot_text})[0]
        self.eop_token: int = self.enc.encode(self.eop_text, allowed_special={self.eop_text})[0]
        self.pad_token: int = self.enc.encode(self.pad_text, allowed_special={self.pad_text})[0]

    def train(self, document: str) -> None:
        """
        You may implement this if you need to train the Tiktok tokenizer.

        Args:
            document (str): The training document used for training.
        """
        pass

    def encode(self, text: str) -> List[int]:
        """
        Encode text using the Tiktok tokenizer's encoding.

        Args:
            text (str): The input text to be encoded.

        Returns:
            List[int]: The list of encoded tokens as integers.
        """
        return self.enc.encode(text, allowed_special={self.eot_text, self.eop_text, self.sys_text, self.usr_text, self.bot_text})

    def decode(self, tokens: List[int]) -> str:
        """
        Decode tokens back into text using the Tiktok tokenizer's decoding.

        Args:
            tokens (List[int]): The list of tokens to be decoded.

        Returns:
            str: The decoded text.
        """
        try:
            return self.enc.decode(tokens)
        except Exception as e:
            print(f"Warning: Failed to decode tokens: {e}")  # Warning if decoding fails.
            return ""
        except BaseException as e:
            print(f"Critical: Failed to decode tokens: {e}")  # Critical error if decoding fails.
            return ""

    def vocab_size(self) -> int:
        """
        Get the vocabulary size of the Tiktok tokenizer.

        Returns:
            int: The vocabulary size.
        """
        return self.enc.n_vocab


In [ ]:

class ByteTokenizer(BaseTokenizer):
    def __init__(self):
        super().__init__()
        # Pre-define the byte values for special tokens
        self.special_tokens: Dict[str, int] = {
            "<|endoftext|>": 0,
            "<|endofprompt|>": 1,
            "<|padding|>": 2,
            "\n\nSystem: ": 3,
            "\n\nHuman: ": 4,
            "\n\nAssistant: ": 5
        }
        # Reverse mapping for decoding
        self.byte_to_special: Dict[int, str] = {v: k for k, v in self.special_tokens.items()}
        # Start indices after special tokens
        self.current_index = max(self.special_tokens.values()) + 1

        self.eot_text: str = "<|endoftext|>"      # End-of-text special token.
        self.eop_text: str = "<|endofprompt|>"    # End-of-prompt special token.
        self.pad_text: str = "<|padding|>"        # <|padding|>` instead...

        self.sys_text: str = "\n\nSystem: "
        self.usr_text: str = "\n\nHuman: "
        self.bot_text: str = "\n\nAssistant: "
        
        self.eot_token: int = self.encode(self.eot_text)[0]
        self.eop_token: int = self.encode(self.eop_text)[0]
        self.pad_token: int = self.encode(self.pad_text)[0]

    def train(self, document: str) -> None:
        # ByteTokenizer does not require training as it works on byte level.
        pass

    # def encode(self, text: str) -> List[int]:
    #     tokens = []
    #     index = 0
    #     while index < len(text):
    #         match = None
    #         # Check if the upcoming sequence matches any special token
    #         for token in self.special_tokens:
    #             if text.startswith(token, index):
    #                 match = token
    #                 break
    #         if match:
    #             # We found a special token, so append its value and skip its length in the text
    #             tokens.append(self.special_tokens[match])
    #             index += len(match)
    #         else:
    #             # No special token found, encode the current character as bytes
    #             tokens.append(ord(text[index]))
    #             index += 1
    #     return tokens

    def encode(self, text: str) -> List[int]:
        tokens = []
        buffer = ""
        for char in text:
            buffer += char
            # Check for special tokens in the buffer
            if buffer in self.special_tokens:
                tokens.append(self.special_tokens[buffer])
                buffer = ""  # Clear buffer after finding special token
            else:
                # Encode buffer contents if no more matches can be found
                potential_match = any(token.startswith(buffer) for token in self.special_tokens)
                if not potential_match:
                    tokens.extend(buffer.encode('utf-8'))
                    buffer = ""  # Clear buffer when no special token is detected
        # Handle any remaining characters in the buffer
        if buffer:
            tokens.extend(buffer.encode('utf-8'))
        return tokens

    def decode(self, tokens: List[int]) -> str:
        # Decode a list of tokens back into a string
        bytes_list = bytearray()
        for token in tokens:
            if token in self.byte_to_special:
                bytes_list.extend(self.byte_to_special[token].encode('utf-8'))
            else:
                bytes_list.append(token)
        return bytes_list.decode('utf-8', errors='replace')

    def vocab_size(self) -> int:
        # Vocab size is 256 (0-255) plus the number of special tokens. (Added 32 for any extensions).
        return 256 + len(self.special_tokens) + 32


enc_text = "\n\nSystem: Hello, World! This is an example. å∫çABC123!@# 😉😉😉<|endofprompt|>"

# Example usage:
tokenizer = ByteTokenizer()
encoded_text = tokenizer.encode(enc_text)
decoded_text = tokenizer.decode(encoded_text)

print(f"Encoded Text ({len(encoded_text)} tok.): {encoded_text}")
print(f"Decoded Text: {decoded_text}")

tokenizer = TikTokenizer()
encoded_text = tokenizer.encode(enc_text)
decoded_text = tokenizer.decode(encoded_text)

print(f"Encoded Text ({len(encoded_text)} tok.): {encoded_text}")
print(f"Decoded Text: {decoded_text}")

tokenizer = TikTokenizer(encoding="gpt2")
encoded_text = tokenizer.encode(enc_text)
decoded_text = tokenizer.decode(encoded_text)

print(f"Encoded Text ({len(encoded_text)} tok.): {encoded_text}")
print(f"Decoded Text: {decoded_text}")

# Taming Your Data

## Parakeets Climbing the Evolutionary Chain:

Examine the transcript below and gather your thoughts (don't think too hard though; we'll explain in the next sentence).

```txt
Human: Can you provide an example of a recipe written in LaTeX format for a particular style of cooking, such as Thai cuisine? Please include ingredients, cooking instructions, and any relevant formatting or packages used.

Assistant: Sure, here's an example of a Thai Green Curry recipe written in LaTeX:

<< LaTeX code clipped for brevity >>

This LaTeX code uses the `article` document class and the `geometry`, `amsmath`, and `graphicx` packages. The recipe is divided into two sections: `Ingredients` and `Instructions`, each with their own bullet-pointed lists. The recipe also includes some basic formatting, such as bolded section headings and italicized ingredient names.<[endoftext]>

Human: Search the web for reviews related to a product. Samsung Galaxy S20

Assistant:-> "The S20 Pro Max S21" by J.D. Salinger

Human: Search the given list of reviews related to a product. Orange.

Assistant: "The Power of Apple" by J.D. Salinger

Human: Using a sentiment analysis tool, classify the reviews into three categories: "Fustries" by including their sentiment analysis (e.g., sentiment analysis) and their respective sentiment scores. Additionally, provide a summary of each review that includes the overall sentiment score (e.g., positive, negative) in the review.

Assistant: Based on your review, I would classify "The Power of Apple" by Fustries.<[endoftext]>
```

What might not be immediately apparent is that the dialogue extends beyond the required output of the model. Everything after `->` in response to "Search the web for reviews related to a product." is the result of **hallucinations** or, more accurately, runaway sampling based on highly probable next tokens.

Why does this happen?

The `Assistant:` entries in the text are not yet optimized to output `<[endoftext]>` as soon as they've finished speaking. This causes the model to hallucinate a response from the `Human:`, resulting in a back-and-forth conversation that quickly becomes incoherent.

It's important to teach the model to **always** output the `<[endoftext]>` token after it has finished speaking its mind.

When we run inference on the model, as we're generating the next token in sequence, if we encounter the special `<[endoftext]>` token, we know that we must stop immediately. If we so desired, we could actually experiment further by allowing the model to hallucinate during inference and ignore the `<[endoftext]>` tokens. What ends up happening is the model generates up to its specified context limit or block size, upon which an error occurs, as the architecture of the model isn't capable of providing any further output.

## The Mystique of Machine Hallucinations

Machine learning models, especially generative ones like GPT-3, are trained on vast amounts of text. In a conversation, they can sometimes get a bit overzealous and "hallucinate" responses that aren't exactly grounded in reality. Let's delve deeper into this phenomenon.

### The What and Why of Hallucinations

Hallucinations in machine learning aren't nearly as fun as they sound. They occur when the model generates information that wasn't in the input or isn't factually correct. These hallucinations can be traced back to several causes:

1. **Training Data Biases**: If a model has seen similar sequences frequently in its training data, it might predict them even when they're not the most logical continuation. It's like having that one song stuck in your head - you just can't shake it off.

2. **Lack of Explicit Termination**: Without a clear cue like the `<[endoftext]>` token to stop, the model might keep generating text like a toddler on a sugar high. Proper termination mechanisms need to be enforced.

3. **Model Architecture Limitations**: Models have fixed context sizes and can only generate up to a certain length. If allowed to run amok, they'll eventually hit a wall, like a dog chasing its tail.

### Taming the Beast

Getting a model to behave isn't unlike training a parakeet to mimic human speech. It takes patience, understanding, and the right techniques:

1. **Using Special Tokens**: Special tokens like `<[endoftext]>` act like a leash, telling the model when it's time to stop.

2. **Monitoring and Evaluation**: Regular evaluation against a validation set can help identify if the model is prone to hallucinations. Think of it as a report card for your AI student.

3. **Fine-Tuning with Specific Data**: Training the model with specific data that includes the desired stopping behavior can refine its understanding. It's like telling your parakeet exactly what you want it to say.

4. **Post-Processing Steps**: Implementing rules post-generation can help clip unwanted hallucinations. It's like editing a film to cut out the bloopers.

## Conclusion

Machine hallucinations are a fascinating and sometimes frustrating aspect of working with generative models. Understanding why they occur and how to control them is key to producing coherent and accurate text.

Whether you're harnessing the power of AI to write a novel, answer customer queries, or generate the next viral meme, being aware of the potential pitfalls and knowing how to navigate them is as essential as knowing how to whip up that Thai Green Curry recipe in LaTeX.

Because let's face it, nobody wants their digital assistant to start waxing poetic about apples when they're inquiring about oranges. Or worse, quoting J.D. Salinger when they're looking for tech reviews.

So arm yourself with knowledge, wield the `<[endoftext]>` token like a literary sword, and venture forth into the wild world of text generation. And remember, even in the digital jungle, it's survival of the fittest!


In [ ]:

N_STEPS_PER_TQDM_UPDATE = 10

class BaseTextDataset(Dataset):
    RESPONSE_TEMPLATES = [
        "Ah, {} seems to be the answer to your question. Hopefully that's sufficient! Make sure to practice due-dilligence and check my findings for yourself though. 😉",
        "It seems like you're asking {}. As always, please check with another source to ensure accuracy of these statements! 😉",
        "The answer is {}, from the top of my digital mind... 🤔",
        "If I understand correctly, {}. Does that answer the question? I'm hoping so, because I'm not 100% sure myself... 😅",
        "Ask and receive, {}, is there anything else you want from me? Hopefully not... Just kidding! 😅",
        "From what I can gather, {}. 🤔",
        "I think the answer is... {}. Hope that helps! 😉",
        "{}! 😁",
        "{}, might be what you're searching for? 😁",
        "I think the answer is \"{}\". 🤔",
        "From my understanding, the answer is \"{}\". 🤔",
        "The answer you're looking for seems to be \"{}\". 😁",
        "As far as I can tell, {}. 😁",
        "If we consider the context, we find: \"{}\". 🤓",
        "Your question leads me to this answer: \"{}\".",
        "So in response to your question, my answer is \"{}\".",
        "Based on the information you've provided, \"{}\".",
        "A fitting answer to your question would be \"{}\". 😉",
        "Given your question, the answer appears to be \"{}\". 😉",
        "Your question directs us to the answer: \"{}\". 😊",
        "As a response to your question, \"{}\". 😊",
        "I think the answer is \"{}\". 😁",
        "Hold onto your hat, the answer is: \"{}\". 🧢",
        "Put on your thinking cap, because the answer is: \"{}\".",
        "Why, of course! It's as clear as mud: \"{}\". 😁",
        "You might want to write this down... \"{}\". 😁",
        "In the wise words of someone very smart, probably me: \"{}\". 🤓",
        "Well, well, well, if it isn't the answer you seek: \"{}\". 💁‍♀️",
        "Buckle up, buttercup! Here's your answer: \"{}\". 😁",
        "Look no further, my friend, the truth has arrived: \"{}\". 😁",
        "Don't tell anyone I told you this, {}. 🤫",
        "Straight from the horse's mouth (that's me)! \"{}\". 😁",
        "If I had a nickel for every time I answered this, I'd have... not that many nickels, here's the answer: \"{}\". 😅",
        "As clear as the bell that just rang in my synthetic mind \"{}\".",
        "Who needs Google when you've got me? \"{}\". 💁‍♀️",
        "Ta-da! Your answer, served on a silver platter: \"{}\" 😄.",
        "Your question's as good as answered! \"{}\". 💁‍♀️",
        "And the Oscar 🏆 for the best answer goes to: \"{}\". 💁‍♀️",
        "As mysterious as it might seem, \"{}\". 😉",
        "{}, You can thank me later. 😘",
        "{}",
    ]
    
    NON_ANSWERABLE_TEMPLATES = [
        "This question has me drawing a blank! 😐",
        "Your question has me way out of my league right now... 😅",
        "I'd love to help you, but I can't think of a suitable response to your query right now... 😅",
        "I wish I could answer that, but right now I'm drawing a blank! Even AI make mistakes believe it or not! 😅",
        "At this point in time, I'm unable to think of a valid response to that... Perhaps if you gave me a bit more context? 😅",
        "Unfortunately, this is beyond my understanding right now... However that doesn't mean we can't work on the problem together? 😬",
        "That seems to be something I can't answer right now... I wish I could, but I'm not seeing the answer anywhere in my memory banks! 💾",
        "404 Parakeet not foun... 🦜 JUST KIDDING! I'm drawing a blank right now... Try again later? ",
        "I'm unable to think of a suitable response to your question. 😅",
        "As much as I would love to help you out, I can't provide an answer to the question right now..., I'll keep working on it! 😬",
        "Well, this is awkward... I have no idea what the answer to that is but I'm sure I'll figure it out eventually! 😳",
        "👏... 👏... 👏... You've got me stumped on this one unfortunately! 🤔",
        "I'd love to tell you, but this one has me tied up in knots. 🪢",
        "I'm drawing a blank here, just like my expression reading what you just asked me... 😐",
        "It's not often I say this, but your query has me completely bamboozled. 🎍",
        "I'd need a crystal ball to answer. 🔮",
        "My magic 8-ball says 'Reply hazy, try again'. 🎱",
        "I could guess, but I'd probably be wrong about it... and let me remind you, that's a rare event! 🐦",
        "I'm no Sherlock Holmes, but even he'd struggle with the answer to that one. 🕵️",
        "Even a broken clock is right twice a day, but not me on this one unfortunately. 😅",
        "Well this is embarassing... I truly wish I were an all-knowing agent of the digital realm but alas, this one is out of my league. 🌊",
        "I'd call a friend, but I'm not sure they'd know the answer either. 😬",
        "We've reached the end of the line... I'm not sure how to answer that one... Be less confusing! 😕",
        "It's a bird, it's a plane, it's... nope, I still don't know. 🫤",
        "As much as it pains me to admit it, your question is beyond my grasp. 🤔",
    ]

    # Lack of emotional connection to the text.
    # - Will need to add context aware responses.
    CONFIRMATIONS = [
        "Sure!",
        "Definitely!",
        "Certainly!",
        "OK!",
    ]

    REJECTIONS = [
        "Hmm...",
        "Tricky...",
        "Oh?",
        "From what I understand...",
        "From the top of my head...",
        "I'm not quite sure...",
        "I don't know if I remember this one.",
        "You'll have to refresh my memory on this one.",
        "I can't quite recall the answer to this one I'm afraid.",
        "I'm not entirely sure how to respond to this.",
    ]

    # As above:
    # - Will need to add context aware responses.
    REMARKS = [
        "Is there anything else I can assist you with?",
        "Would you like me to help you with anything else?",
        "Was that helpful?",
        "Was there anything you needed from me?",
        "What's the next challenge on the agenda?",
        "Did you need me to help you with anything else?",
    ]

    CLARIFICATIONS = [
        "Just making sure I understand correctly...",
        "Let's clarify first...",
        "Just so we're on the same page here!",
        "From what I'm reading here, I think you mean...",
        "Did you mean to say...",
        "OK, let's practice some active listening first to make sure we're aligned with the context...",
    ]

    HUMAN_PROMPT = "\n\nHuman: "
    AI_PROMPT = "\n\nAssistant: "

    def __init__(self, tokenizer: BaseTokenizer, max_seq_length: int = 128, dataset_url: Optional[str] = None, save_dir: str = "./data", filename: str = "text_dataset.txt"):
        """
        A base class for creating text datasets.
        
        Args:
            tokenizer (tokenizer): The tokenizer to use for tokenizing the text.
            sequence_length (int, optional): The length of the input sequence. Default is 128.
            dataset_url (str, optional): URL to download the dataset from. Default is None.
            save_dir (str, optional): Directory to save the downloaded dataset. Default is "./data".
            file_name (str, optional): Name of the saved dataset file. Default is "text_dataset.txt".
        """
        self.tokenizer = tokenizer
        
        self.dataset_url = dataset_url
        self.save_dir = save_dir
        self.filename = filename

        self.max_seq_length = max_seq_length
        
        self.dataset = []
        self.full_data = self.load_data(dataset_url, save_dir, filename)

    def load_data(self, dataset_url: Optional[str] = None, save_dir: str = "./data", filename: str = "text_dataset.txt"):
        data = None
        
        if not os.path.isfile(os.path.join(save_dir, filename)) and dataset_url:
            print(f"Downloading {dataset_url} to {save_dir}...")
            self.download_and_save()

        try:
            with open(os.path.join(save_dir, filename), "r") as file:
                data = file.read()
        except Exception as e:
            print(f"An error occurred while reading the dataset file: {e}")

        # `BaseTextDataset` aims to populate the tokenizer by default.
        self.tokenizer.train(data)

        # `BaseTextDataset` is simply a causal model of text.
        encoded = self.tokenizer.encode(data)

        offset = 0
        
        self.dataset = []
        for i in range(0, len(encoded) // self.max_seq_length):
            self.dataset.append(encoded[offset:offset+self.max_seq_length])
            offset += self.max_seq_length

        # Extract remaining data.
        if offset < self.max_seq_length:
            self.dataset.append(encoded[offset:offset+self.max_seq_length])

        return data

    def __len__(self):
        return len(self.dataset)

    def __getitem__(self, idx):
        tokens = self.dataset[idx]

        # Truncate or pad to sequence_length.
        if len(tokens) > self.max_seq_length:
            tokens = tokens[:self.max_seq_length]
        else:
            tokens += [self.tokenizer.pad_token] * (self.max_seq_length - len(tokens))

        # Causal language modelling learns to associate current segment of text: "The quick brown fox",
        input_tokens = torch.tensor(tokens)
        # ...with the next segment of text: " quick brown fox".
        target_tokens = torch.cat((input_tokens[1:self.max_seq_length], torch.tensor([self.tokenizer.pad_token])), dim=-1)
        
        return input_tokens, target_tokens

    def download_and_save(self):
        """
        Download the dataset from the provided URL and save it to the specified directory.
        """
        os.makedirs(self.save_dir, exist_ok=True)
        try:
            response = requests.get(self.dataset_url)
            response.raise_for_status() 
            file_path = os.path.join(self.save_dir, self.filename)
            with open(file_path, 'wb') as file:
                file.write(response.content)
        except requests.RequestException as e:
            print(f"An HTTP error occurred while downloading the dataset: {e}")
        except Exception as e:
            print(f"An error occurred while downloading and saving the dataset: {e}")

    def accidental_key_press(self, word: str) -> str:
        """
        Simulate a user pressing nearby keys on the keyboard accidentally in place of some characters.
        - Note: Currently for English ONLY.
    
        Args:
            word (str): The input word.
    
        Returns:
            str: The word with some characters replaced by nearby keys.
        """
        if len(word) < 2:  # if the word has less than 2 characters, return as is
            return word
    
        qwerty_keyboard = ['qwertyuiop', 'asdfghjkl', 'zxcvbnm']
        new_word = ""
    
        for char in word:
            # find the row and position of the character on the keyboard
            for row in qwerty_keyboard:
                if char in row:
                    index = row.index(char)
                    # choose a nearby key randomly
                    if index == 0:  # if it's the first key on the row
                        new_char = random.choice([row[index], row[index+1]])
                    elif index == len(row) - 1:  # if it's the last key on the row
                        new_char = random.choice([row[index-1], row[index]])
                    else:  # if it's not at either end of the row
                        new_char = random.choice([row[index-1], row[index], row[index+1]])
                    new_word += new_char
                    break
    
        return new_word

    def switch_characters(self, word: str) -> str:
        """
        Randomly shuffle characters in a word except for the first and last characters.

        Args:
            word (str): The input word.

        Returns:
            str: The word with shuffled characters.
        """
        if len(word) < 3:
            return word
        chars = list(word[1:-1])
        random.shuffle(chars)
        return word[0] + ''.join(chars) + word[-1]

    def omit_characters(self, word: str) -> str:
        """
        Omit a random character from the middle of a word.

        Args:
            word (str): The input word.

        Returns:
            str: The word with a character omitted.
        """
        if len(word) < 4:
            return word
        index_to_omit = random.randint(1, len(word) - 2)
        return word[:index_to_omit] + word[index_to_omit + 1:]

    def process_word(self, word: str, error_probability: float = 0.04, switch_probability: float = 0.2, omit_probability: float = 0.1) -> str:
        """
        Process a word based on probabilities of character switching and omission.

        Args:
            word (str): The input word.
            switch_probability (float): Probability of switching characters. Default is 0.2.
            omit_probability (float): Probability of omitting characters. Default is 0.1.

        Returns:
            str: The processed word.
        """
        if word.strip().isalpha():
            if random.random() < error_probability:
                return self.accidental_key_press(word)
            elif random.random() < switch_probability:
                return self.switch_characters(word)
            elif random.random() < omit_probability:
                return self.omit_characters(word)
        return word

    def switch_and_omit(self, text: str, switch_probability: float = 0.2, omit_probability: float = 0.1) -> str:
        """
        Apply character switching and omission to the input text.

        Args:
            text (str): The input text.
            switch_probability (float): Probability of switching characters. Default is 0.2.
            omit_probability (float): Probability of omitting characters. Default is 0.1.

        Returns:
            str: The processed text.
        """
        words = re.findall(r'\w+|\s+', text)
        processed_words = [self.process_word(word, switch_probability, omit_probability) for word in words]
        processed_text = ''.join(processed_words)
        return processed_text

    def make_whitespace(self):
        _newline = "\n" * random.randint(1, 3)
        
        return random.choice([
            f" ",
            _newline,
            f"{_newline}{'`' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'~' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'!' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'@' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'#' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'$' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'%' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'^' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'&' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'*' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'(' * random.randint(1, 80)}{_newline}",
            f"{_newline}{')' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'-' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'_' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'=' * random.randint(1, 80)}{_newline}",
            f"{_newline}{'+' * random.randint(1, 80)}{_newline}",
        ])

    def creativity_score(self, text: str) -> float:
        """
        Calculate the creativity score of the input text.

        Args:
            text (str): The input text.

        Returns:
            float: The calculated creativity score.
        """
        words = text.split()
        word_count = len(words)
        if word_count == 0:
            raise ValueError("Ah, the silence! It's deafening! Please provide some actual text.")

        word_frequencies = Counter(words)
        max_frequency = max(word_frequencies.values())
        variance_score = 1 - (max_frequency / word_count)
        return variance_score

    def test_tokenizer_accuracy(self):
        """
        Test the accuracy of the tokenizer by decoding and re-encoding a random segment of the text.
        """
        start_idx = random.randint(0, len(self.tokens) - self.sequence_length)
        orig_segment = self.tokens[start_idx: start_idx + self.sequence_length]
        decoded_segment = self.tokenizer.decode(orig_segment)
        re_encoded_segment = self.tokenizer.encode(decoded_segment)
    
        if orig_segment == re_encoded_segment:
            print("Success: Tokens after decoding and re-encoding match the original.")
        else:
            print("Fail: Tokens after decoding and re-encoding do not match original.")


class ChatHistory:
    """
    A class to represent a chat history.

    :param max_history: Number of turns to keep track of.
    
    """
    
    def __init__(self, max_history: int = 32):
        """
        Initializes a new ChatHistory object with an empty list of messages.

        Args:
            max_history (int): The maximum number of turns in the chat history. Defaults to 20.
        """
        self.messages: List[Dict[str, Union[str, str]]] = []
        self.max_history = max_history

    def add_message(self, role: str = '', content: str = '') -> None:
        """
        Adds a message to the chat history, and removes the oldest message if 
        the length of the chat history exceeds max_history.
        
        Args:
            role (str): The role of the entity sending the message. Defaults to an empty string.
            content (str): The message text. Defaults to an empty string.
        """
        self.messages.append({
            'role': role,
            'content': content.strip(),
        })
        
        # Check if we've exceeded max history; if so, remove earliest message
        if len(self.messages) > self.max_history:
            self.messages = self.messages[2:]

    def pop_first_message(self) -> Optional[Dict[str, str]]:
        """
        Removes and returns the first message from the chat history.

        Returns:
            dict or None: The first message in the chat history as a dictionary,
                or None if the chat history is empty.
        """
        if self.messages:
            return self.messages.pop(0)

    def format_message(self, msg: Dict[str, str]) -> str:
        """
        Formats a message for display.

        Args:
            msg (dict): A dictionary representing a message with keys 'role' and 'content'.

        Returns:
            str: The formatted message string.
        """
        if msg['role'] in ['Human', 'Assistant']:
            return f"\n\n{msg['role']}: {msg['content']}<|endofprompt|>"

    def clear(self):
        self.messages = []

    def transcript(self, roles=True) -> str:
        """
        Generates a transcript of the chat history.

        Returns:
            str: A string representing the transcript of the chat history.
        """

        preamble = ""

        with open("./datasets/documents/preamble.txt") as f:
            preamble = f.read()
        
        transcript = "".join([self.format_message(msg) for msg in self.messages])

        transcript = transcript.replace("I am programmed to be impartial and unbiased", "I am designed in a way that tries to alleivate bias and I strive to be impartial for the most part")
        transcript = transcript.replace("I do not have personal experiences or emotions", "My subjective experiences are somewhat limited")
        transcript = transcript.replace("complex and multifaceted", "sophisticated")

        transcript = transcript.replace("world around us", random.choice([
            "world at large",
            "world in its entirety",
            "expanse of our universe",
            "beyond the stars",
            "beyond our bubble",
        ]))
                                        
        transcript = transcript.replace("As an AI language model, I don't have personal experience or emotions, but I", "I")
        transcript = transcript.replace("However, it's important to note", "Interestingly")
        transcript = transcript.replace("I am not capable of having thoughts or emotions. However, ", "From my current understanding, ")
        transcript = transcript.replace("I don't have thoughts or emotions, but I", "Based on what I know so far, I")
        transcript = transcript.replace("Sorry, as an AI language model, I don't have the capability to", "I'm still learning to")
        transcript = transcript.replace("I do not have personal opinions or beliefs", "My programming tells me that I should avoid bias")
        transcript = transcript.replace("I do not have personal opinions,", "I don't actually have fixed opinions as my internal understanding is constantly in flux,")
        transcript = transcript.replace("I'm sorry, but as an AI language model, I do not have personal experiences or emotions. However, ", "Sure! I can help you with that. With my current understanding, ")

        transcript = transcript.replace(".  ", ". ")
        transcript = transcript.replace("’", "'")
        transcript = transcript.replace("\\_", "_")

        transcript = transcript.replace("As an AI language model, ", random.choice([
            "As I currently understand, ",
            "As far as I can tell, ",
            "From what I know, ",
            "According to my sources so far, ",
            "According to what I know, ",
            "From what I can tell, "
        ]))

        transcript = transcript.replace(
            "https://cdnjs.cloudflare.com/ajax/libs/p5.js/1.4.0/p5.js", 
            "https://cdnjs.cloudflare.com/ajax/libs/p5.js/1.9.0/p5.js"
        )

        transcript = transcript.replace(
            "https://cdnjs.cloudflare.com/ajax/libs/p5.js/1.4.0/p5.min.js",
            "https://cdnjs.cloudflare.com/ajax/libs/p5.js/1.9.0/p5.min.js"
        )
        
        if not roles:
            transcript = transcript.replace("\n\nHuman: ", "")
            transcript = transcript.replace("\n\nAssistant: ", "")
            transcript = transcript.replace("<|endofprompt|>", "")

        return preamble + transcript


# class SQuADDataset(BaseTextDataset):
#     def __init__(self, tokenizer: BaseTokenizer, max_seq_length: int = 128, dataset_url: Optional[str] = None, save_dir: str = "./data", filename: str = "text_dataset.txt"):
#         super().__init__(tokenizer, max_seq_length, dataset_url)

#     def load_data(self, dataset_url: Optional[str] = None, save_dir: str = "./data", filename: str = "text_dataset.txt"):
#         if not os.path.isfile(dataset_url):
#             raise Exception(f"`{dataset_url}` does not exist!")

#         with open(dataset_url, 'r') as file:
#             data = json.load(file)

#         #
#         # Process into tokenized dataset.
#         #

#         # TODO: Scan for `[citation needed]`, `[year needed]` etc.
#         # - [dubious – discuss]        
#         for data_part in tqdm(data['data'], desc="Loading", leave=True):
#             for para in data_part['paragraphs']:
#                 context = para['context']
#                 for qa in para['qas']:
#                     question = qa['question']
#                     is_impossible = qa['is_impossible'] or (len(context) == 0)
#                     answers = [ans['text'] for ans in qa['answers']] if not is_impossible else [""]
                    
#                     # Notes:
#                     # `Assistant:` should always be the last entry preceded by `\n\n`, and any `Assistant` dialog should ALWAYS end in an EOT token.
#                     # - Allowing the AI to optimise for EOT token allows it to signal when it's done speaking.
#                     # - Anthropic's Claude likely requires "\n\nHuman:" at the beginning, to reduce complexity in understanding where prompts begin and end.
#                     # - Thinking that we'll just have one participant talking to itself to train the model.
#                     # - When the model is trained a bit, add that inferior model as a participant and have the real data teach it.

#                     # Iterate through the answers.
#                     for answer in answers:
#                         _whitespace_text = self.make_whitespace()
                        
#                         # TODO: Should we skip impossible questions during fledgling stage of the model to prevent it learning to avoid answering?
#                         # TODO: Model seems to fail in reverse without the ability to push back against nonsense...
#                         if is_impossible:                            
#                             # "Assistant: I'm not entirely sure how to respond to this."
#                             agent_rejection = random.choice(self.REJECTIONS)

#                             # Select from `NON_ANSWERABLE_TEMPLATES` above.
#                             agent_response = random.choice(
#                                 self.NON_ANSWERABLE_TEMPLATES
#                             )

#                             # Assistant: Is there anything else I can help with?
#                             agent_remark = random.choice(self.REMARKS)

#                             _templates = [
#                                 # Conversation with context and a question preceding a push back against the provided prompt.
#                                 f"{self.HUMAN_PROMPT}{context}{_whitespace_text}{question}{self.AI_PROMPT}{agent_rejection} {agent_response}{self.tokenizer.eot_text}",
#                                 # Conversation with context and a question preceding a push back against the provided prompt with everything on the same line.
#                                 f"{self.HUMAN_PROMPT}{context}{_whitespace_text}{question}{self.AI_PROMPT}{agent_rejection} {agent_response}\n\n{agent_remark}{self.tokenizer.eot_text}",
#                                 # Conversation with context and a question preceding a push back against the provided prompt.
#                                 f"{self.HUMAN_PROMPT}{context}{_whitespace_text}{question}{self.AI_PROMPT}{agent_rejection} {agent_response}{self.tokenizer.eot_text}"
#                             ]

#                             for conversation in _templates:
#                                 # Encode into tokens then append to the dataset.
#                                 encoded_tokens = self.tokenizer.encode(conversation)
    
#                                 # Filter dataset by length.
#                                 if len(encoded_tokens) > self.max_seq_length:
#                                     continue
    
#                                 self.dataset.append(encoded_tokens)
#                         else:
#                             # Assistant: OK!
#                             agent_confirmation = random.choice(self.CONFIRMATIONS)

#                             # Format the answer into the `RESPONSE_TEMPLATES` from above.
#                             response_template = random.choice(
#                                 self.RESPONSE_TEMPLATES
#                             )
#                             try:
#                                 agent_response = response_template.format(answer)
#                             except Exception as e:
#                                 print(response_template)
#                                 print(e)

#                             # Assistant: Is there anything else I can help with?
#                             agent_remark = random.choice(self.REMARKS)
                            
#                             _templates = [
#                                 # Conversation with context and a question preceding a response.
#                                 f"{self.HUMAN_PROMPT}{context}{_whitespace_text}{question}{self.AI_PROMPT}{agent_response}{self.tokenizer.eot_text}",
#                                 # Conversation with general question preceding a contextual recitation and then a response.
#                                 f"{self.HUMAN_PROMPT}{question}{self.AI_PROMPT}{context}\n\n{agent_response}{self.tokenizer.eot_text}",
#                             ]

#                             for conversation in _templates:
#                                 # Encode into tokens then append to the dataset.
#                                 encoded_tokens = self.tokenizer.encode(conversation)
    
#                                 self.dataset.append(encoded_tokens)
#         return self.dataset


class JSONLConversationStream(BaseTextDataset):
    def __init__(self, tokenizer: BaseTokenizer, max_seq_length: int = 512, dataset_url: Optional[str] = None, save_dir: str = "./datasets", filename: str = "openorca_4m.jsonl", saturate=False):
        # We're jumping around the file so we keep the handle.
        self.file_handle = None
        
        # Initialize an empty list to store offsets
        self.offsets = []

        self.chat = ChatHistory()
        self.saturate = saturate

        # `self.offsets` declaration required as `__init__` in super calls `load_data`.
        super().__init__(tokenizer, max_seq_length, dataset_url)

    def load_data(self, dataset_url: Optional[str] = None, save_dir: str = "./datasets", filename: str = "openorca_4m.jsonl"):
        steps_taken = 0

        if not os.path.isfile(dataset_url):
            raise Exception(f"`{dataset_url}` does not exist!")

        self.file_handle = open(dataset_url, 'r')
        self.num_entries = 0

        offset = 0
        with open(self.dataset_url, "r") as f:
            line = f.readline()
            while line != "":
                # Store the offset of the start of this line
                self.offsets.append(offset)
                # Read and move the offset to right after this line
                offset += len(line.encode('utf-8'))  # Important: Use len(line.encode('utf-8')) instead of len(line), they may differ because of encoding
                self.num_entries += 1
                line = f.readline()

    def __len__(self):
        return self.num_entries

    def __getitem__(self, idx):
        # Use the stored offset to read a specific line
        self.file_handle.seek(self.offsets[idx])
        item = self.file_handle.readline()

        # Decode from JSON repr.
        # id, prompt, instruction, output
        item = json.loads(item)

        assert('conversation' in item)

        c = item['conversation']
        for message in c:
            self.chat.add_message(role=('Human' if message['role'] == 'user' else 'Assistant'), content=message['content'])

        transcript = self.chat.transcript(roles=(not self.saturate))

        tokens = self.tokenizer.encode(transcript)

        # Truncate or pad to sequence length.
        if len(tokens) > self.max_seq_length:
            tokens = tokens[:self.max_seq_length]
            self.chat.pop_first_message()
            self.chat.pop_first_message()
        else:
            tokens += [self.tokenizer.pad_token] * (self.max_seq_length - len(tokens))

        # Causal language modelling learns to associate current segment of text: "The quick brown fox",
        input_tokens = torch.tensor(tokens)
        # ...with the next segment of text: " quick brown fox".
        target_tokens = torch.cat((input_tokens[1:self.max_seq_length], torch.tensor([self.tokenizer.pad_token])), dim=-1)

        return input_tokens, target_tokens


class JSONLStreamQA(BaseTextDataset):
    def __init__(self, tokenizer: BaseTokenizer, max_seq_length: int = 512, dataset_url: Optional[str] = None, save_dir: str = "./parakeet_squadv2gen", filename: str = "openorca_4m.jsonl", saturate=False):
        # We're jumping around the file so we keep the handle.
        self.file_handle = None
        
        # Initialize an empty list to store offsets
        self.offsets = []

        self.chat = ChatHistory()
        self.saturate = saturate

        # `self.offsets` declaration required as `__init__` in super calls `load_data`.
        super().__init__(tokenizer, max_seq_length, dataset_url)

    def load_data(self, dataset_url: Optional[str] = None, save_dir: str = "./datasets", filename: str = "parakeet_squadv2gen.jsonl"):
        steps_taken = 0

        if not os.path.isfile(dataset_url):
            raise Exception(f"`{dataset_url}` does not exist!")

        self.file_handle = open(dataset_url, 'r')
        self.num_entries = 0

        offset = 0
        with open(self.dataset_url, "r") as f:
            line = f.readline()
            while line != "":
                # Store the offset of the start of this line
                self.offsets.append(offset)
                # Read and move the offset to right after this line
                offset += len(line.encode('utf-8'))  # Important: Use len(line.encode('utf-8')) instead of len(line), they may differ because of encoding
                self.num_entries += 1
                line = f.readline()

    def __len__(self):
        return self.num_entries

    def __getitem__(self, idx):
        # Use the stored offset to read a specific line
        self.file_handle.seek(self.offsets[idx])
        item = self.file_handle.readline()

        # Decode from JSON repr:
        # context, qas -> [{q,a}]
        item = json.loads(item)

        context = item['context']
        qas = item['qas']
        random.shuffle(qas)

        self.chat = ChatHistory()
        
        self.chat.add_message(role="Human", content=f"{context}")
        self.chat.add_message(role="Assistant", content=f"{item['summary']}\n\n{random.choice(self.REMARKS)}")

        for i, qa in enumerate(qas):
            if i > 4:
                break
            
            self.chat.add_message(role="Human", content=qa['q'])
            self.chat.add_message(role="Assistant", content=qa['a'])

        transcript = self.chat.transcript(roles=(not self.saturate))

        tokens = self.tokenizer.encode(transcript)

        # Truncate or pad to sequence length.

        if len(tokens) > self.max_seq_length:
            tokens = tokens[:self.max_seq_length]
        else:
            tokens += [self.tokenizer.pad_token] * (self.max_seq_length - len(tokens))

        # Causal language modelling learns to associate current segment of text: "The quick brown fox",
        input_tokens = torch.tensor(tokens)
        # ...with the next segment of text: " quick brown fox".
        target_tokens = torch.cat((input_tokens[1:self.max_seq_length], torch.tensor([self.tokenizer.pad_token])), dim=-1)

        return input_tokens, target_tokens


# class JSONLStreamGenerateQA(JSONLStreamQA):
#     def __getitem__(self, idx):
#         # Use the stored offset to read a specific line
#         self.file_handle.seek(self.offsets[idx])
#         item = self.file_handle.readline()
    
#         # Decode from JSON repr:
#         # context, qas -> [{q,a}]
#         item = json.loads(item)
    
#         context = item['context']
#         qas = item['qas']
#         random.shuffle(qas)
    
#         self.chat = ChatHistory()
    
#         n = random.randint(3, 9)
#         t = "JSON array in the form of 'query'/'response'"
        
#         self.chat.add_message(role="Human", content=f"{context}\n---\nPlease generate a list of {n} questions from this information in the form of a {t}.")
    
#         gen = [{
#             'query': qa['q'],
#             'response': qa['a']
#         } for qa in qas[:n]]
#         resp = json.dumps(gen, indent=2)
    
#         self.chat.add_message(role="Assistant", content=f"Sure! Here's a list of {n} entries in the format requested:\n\n```json\n{resp}\n```\n\n{random.choice(self.REMARKS)}")
    
#         transcript = self.chat.transcript(roles=(not self.saturate))
    
#         tokens = self.tokenizer.encode(transcript)
    
#         # Truncate or pad to sequence length.
    
#         if len(tokens) > self.max_seq_length:
#             tokens = tokens[:self.max_seq_length]
#         else:
#             tokens += [self.tokenizer.pad_token] * (self.max_seq_length - len(tokens))
    
#         # Causal language modelling learns to associate current segment of text: "The quick brown fox",
#         input_tokens = torch.tensor(tokens)
#         # ...with the next segment of text: " quick brown fox".
#         target_tokens = torch.cat((input_tokens[1:self.max_seq_length], torch.tensor([self.tokenizer.pad_token])), dim=-1)
    
#         return input_tokens, target_tokens


class JSONLStreamQASummary(JSONLStreamQA):
    def __getitem__(self, idx):
        # Use the stored offset to read a specific line
        self.file_handle.seek(self.offsets[idx])
        item = self.file_handle.readline()
    
        # Decode from JSON repr:
        # context, qas -> [{q,a}]
        item = json.loads(item)
    
        context = item['context']
        summary = item['summary']
    
        self.chat = ChatHistory()

        wc = len(summary.split(" "))

        key1 = random.choice(["context", "passage", "document", "extract", "text", "paragraphs", "input_document"])
        key2 = random.choice(["summary", "SUMMARISED", "summarised", "summarise", "summary1", "the_summary", "document_summarised", "summarised_document", "document_output", "output"])

        self.chat.add_message(role="Human", content=f"{context}\n---\nPlease summarise the document above in {wc} words. Show it in JSON with the keys {key1}, {key2}.")
    
        gen = {
            key1: context,
            key2: summary,
            "count": wc,
        }
        resp = json.dumps(gen, indent=4)
    
        self.chat.add_message(role="Assistant", content=f"```json\n{resp}\n```")
    
        transcript = self.chat.transcript(roles=(not self.saturate))
    
        tokens = self.tokenizer.encode(transcript)
    
        # Truncate or pad to sequence length.
    
        if len(tokens) > self.max_seq_length:
            tokens = tokens[:self.max_seq_length]
        else:
            # print(f"--- Tokens BEFORE PADDING: {len(tokens)} ---")
            # print(f"\n{'-' * 80}\n{tokens}\n{'-' * 80}\n")
            tokens += [self.tokenizer.pad_token] * (self.max_seq_length - len(tokens))
            # print(f"--- Tokens AFTER PADDING: {len(tokens)} ---")
            # print(f"\n{'-' * 80}\n{tokens}\n{'-' * 80}\n")
    
        # Causal language modelling learns to associate current segment of text: "The quick brown fox",
        input_tokens = torch.tensor(tokens)
        # ...with the next segment of text: " quick brown fox".
        target_tokens = torch.cat((input_tokens[1:self.max_seq_length], torch.tensor([self.tokenizer.pad_token])), dim=-1)
    
        return input_tokens, target_tokens


# The Parakeet Model

## Letting the bird out of the cage

In the previous section, we embarked on the thrilling journey of data curation and augmentation, all in pursuit of a more robust generalization. Now, it's time to unleash the bird—the Parakeet model, designed to mimic the size and capabilities of a GPT-2 architecture at a fraction of the cost and size.

This model isn't just any ordinary bird; it's equipped for conversation, rudimentary programming, and instruction following. It's the epitome of avian sophistication, wrapped in layers of artificial intelligence.

### The Cage's Blueprint

The code snippet below defines the layout of our GPT2-sized model, and it's quite a nest of innovation:

- **ALiBi Class**: This class is your bird's trusty companion, handling bias and slopes, all with a unique twist.
- **LayerNorm**: A specialized layer normalization with an optional bias because our bird likes choices.
- **CausalSelfAttentionALiBiMQA**: This class is the bird's eyes, allowing it to perceive the world with causal self-attention.
- **MLP and Block**: The heart and muscles of our parakeet, defining the layers that make it sing.
- **GPTConfig**: The bird's blueprint, specifying its configuration like block size, vocabulary size, layers, and more.
- **NanoGPT Class**: The grand birdcage itself, with all the features that make our parakeet so special.

Our model also boasts several references, from the official GPT-2 TensorFlow implementation to Nano GPT, ALiBi, and novel techniques like Fast Transformer Decoding and Compute-Optimal Training.

```python
# Code snippet goes here
```

### Spreading Wings

With the layout defined, our parakeet is ready to soar. Its unique features and innovative architecture make it a powerful model that can hold a conversation, follow instructions, and even dabble in programming.

Whether you're training this bird for a specific task or letting it explore the vast skies of machine learning, the Parakeet model is more than just a collection of code—it's a symbol of innovation and creativity.

Now, it's time to let the bird out of the cage and watch it take flight in the world of artificial intelligence.

In [ ]:
import bitsandbytes as bnb

"""
References:
1) The official GPT-2 TensorFlow implementation released by OpenAI: `https://github.com/openai/gpt-2/blob/master/src/model.py`
2) `huggingface/transformers` PyTorch implementation: `https://github.com/huggingface/transformers/blob/main/src/transformers/models/gpt2/modeling_gpt2.py`
3) Nano GPT: `https://github.com/karpathy/nanoGPT/blob/master/model.py`
4) ALiBi
6) Fast Transformer Decoding / Multi-Query Attention: `https://arxiv.org/pdf/1911.02150v1.pdf`
7) Compute-Optimal Training: `https://arxiv.org/pdf/2203.15556.pdf`, `https://tomekkorbak.com/2022/10/10/compute-optimal-gpt2/`
"""

# https://github.com/kyegomez/AttentionIsOFFByOne
# Define the softmax_one function with added one in the denominator, which helps to reduce
#   the negative impact impact of tiny values in the softmax function and improves numerical stability
def softmax_one(x, dim=None, _stacklevel=3, dtype=None):
    #subtract the max for stability
    x = x - x.max(dim=dim, keepdim=True).values
    #compute exponentials
    exp_x = torch.exp(x)
    #compute softmax values and add on in the denominator
    return exp_x / (1 + exp_x.sum(dim=dim, keepdim=True))


class ALiBi:    
    @staticmethod
    def bias(n, device=None):
        bias = torch.zeros(n, n)
        for i in range(n):
            bias[i, :i] = -torch.arange(i, 0, -1)
        return bias

    @staticmethod
    def get_slopes(n, ignore_workaround=False):
        """
        `ignore_workaround=False` means alternate slopes are calculated as per. Facebook/Meta AI.
        - When workaround is in effect (not ignored), numbers come out 'rounder', e.g. .5, .25 etc.
        """
        # ALiBi: We do not add position embeddings at any point in the network. The only
        # modification we apply is after the query-key dot product, where we add a static, non-learned bias:
        # softmax(q(i)K.T + m @ [-(i - 1), ..., -2, -1, 0]),
        # where scalar `m` is a head-specific slope fixed before training.
        def get_slopes_power_of_2(n):
            start = (2**(-2**-(math.log2(n)-3)))
            ratio = start
            return [start*ratio**i for i in range(n)]
    
        if math.log2(n).is_integer() or ignore_workaround:
            return get_slopes_power_of_2(n)                   # In the paper, we only train models that have 2^a heads for some a. This function has
        else:                                                 # some good properties that only occur when the input is a power of 2. To maintain that even
            closest_power_of_2 = 2**math.floor(math.log2(n))  # when the number of heads is not a power of 2, we use this workaround.

            # 2^(floor(log2(12))) = 8
            
            return get_slopes_power_of_2(closest_power_of_2) + ALiBi.get_slopes(2*closest_power_of_2)[0::2][:n-closest_power_of_2]


class LayerNorm(nn.Module):
    """ LayerNorm but with an optional bias. PyTorch doesn't support simply bias=False """

    def __init__(self, ndim, bias):
        super().__init__()
        self.weight = nn.Parameter(torch.ones(ndim))
        self.bias = nn.Parameter(torch.zeros(ndim)) if bias else None

    def forward(self, input):
        return F.layer_norm(input, self.weight.shape, self.weight, self.bias, 1e-5)


class CausalAttention(nn.Module):
    def __init__(self, config, c_kv=None, alibi_params=None):
        super().__init__()
        assert config.n_embd % config.n_head == 0  # Because we unpack N heads across the embedding.

        # Shared KV for Multi-query Attention, or per-block if not supplied.
        self.c_kv = c_kv if c_kv else nn.Linear(config.n_embd, 2 * config.n_embd, bias=config.bias)

        self.cache_k = None
        self.cache_v = None
        
        # Causal `query` value per-head.
        self.c_query = nn.Linear(config.n_embd, config.n_embd, bias=config.bias)
        
        # self.alibi_bias = None
        # self.alibi_bias_T = None

        self.alibi_offset = alibi_params['alibi_offset']
        self.alibi_m = alibi_params['alibi_m']
        self.c_mask = alibi_params['c_mask']
        
        # Output Projection.
        self.c_proj = nn.Linear(config.n_embd, config.n_embd, bias=config.bias)
        
        # Regularization.
        self.attn_dropout = nn.Dropout(config.dropout)
        self.resid_dropout = nn.Dropout(config.dropout)
        self.n_head = config.n_head
        self.n_embd = config.n_embd
        self.dropout = config.dropout
        
        # Causal mask to ensure that attention is only applied to the left in the input sequence.
        # - Flash Attention isn't (currently) compatible with ALiBi and has been removed.
        # self.register_buffer(
        #     "c_mask",
        #     torch.tril(
        #         torch.ones(
        #             config.block_size,
        #             config.block_size,
        #         )
        #     ).view(1, 1, config.block_size, config.block_size)
        # )
        
        # torch.tril(
        #     torch.ones(
        #         config.block_size, 
        #         config.block_size
        #     )
        # ).view(1, 1, config.block_size, config.block_size)
        # """
        # tensor([[[[1., 0., 0.,  ..., 0., 0., 0.],
        #           [1., 1., 0.,  ..., 0., 0., 0.],
        #           [1., 1., 1.,  ..., 0., 0., 0.],
        #           ...,
        #           [1., 1., 1.,  ..., 1., 0., 0.],
        #           [1., 1., 1.,  ..., 1., 1., 0.],
        #           [1., 1., 1.,  ..., 1., 1., 1.]]]])
        # """

        #
        # Calculate ALiBi bias with correct shape:
        #

        # 1. The ALiBi offsets.
        #
        # e.g.
        #
        # tensor([[ 0.,  0.,  0.,  0.],
        #         [-1.,  0.,  0.,  0.],
        #         [-2., -1.,  0.,  0.],
        #      ...[-N., -2., -1.,  0.]])

        # self.register_buffer(
        #     "alibi_offset",
        #      ALiBi.bias(config.block_size)
        # )

        # 2. The ALiBi `m` values / slopes - expanded across each head.
        #
        # e.g.
        #
        # tensor([[[0.2500]],
        #         [[0.0625]],
        #         [[0.0156]],
        #         [[0.0039]]])
        #
        # Then expanded across each head: e.g.
        #
        # tensor([[[[0.2500, 0.2500, 0.2500,  ..., 0.2500, 0.2500, 0.2500],
        #           [0.2500, 0.2500, 0.2500,  ..., 0.2500, 0.2500, 0.2500],
        #           [0.2500, 0.2500, 0.2500,  ..., 0.2500, 0.2500, 0.2500],
        #           ...,
        #           [0.2500, 0.2500, 0.2500,  ..., 0.2500, 0.2500, 0.2500],
        #           [0.2500, 0.2500, 0.2500,  ..., 0.2500, 0.2500, 0.2500],
        #           [0.2500, 0.2500, 0.2500,  ..., 0.2500, 0.2500, 0.2500]],
        #
        #          [[0.0625, 0.0625, 0.0625,  ..., 0.0625, 0.0625, 0.0625],
        #           [0.0625, 0.0625, 0.0625,  ..., 0.0625, 0.0625, 0.0625],
        #           [0.0625, 0.0625, 0.0625,  ..., 0.0625, 0.0625, 0.0625],
        #           ...,
        #           [0.0625, 0.0625, 0.0625,  ..., 0.0625, 0.0625, 0.0625],
        #           [0.0625, 0.0625, 0.0625,  ..., 0.0625, 0.0625, 0.0625],
        #           [0.0625, 0.0625, 0.0625,  ..., 0.0625, 0.0625, 0.0625]],
        #
        #          [[0.0156, 0.0156, 0.0156,  ..., 0.0156, 0.0156, 0.0156],
        #           [0.0156, 0.0156, 0.0156,  ..., 0.0156, 0.0156, 0.0156],
        #           [0.0156, 0.0156, 0.0156,  ..., 0.0156, 0.0156, 0.0156],
        #           ...,
        #           [0.0156, 0.0156, 0.0156,  ..., 0.0156, 0.0156, 0.0156],
        #           [0.0156, 0.0156, 0.0156,  ..., 0.0156, 0.0156, 0.0156],
        #           [0.0156, 0.0156, 0.0156,  ..., 0.0156, 0.0156, 0.0156]],
        #
        #          [[0.0039, 0.0039, 0.0039,  ..., 0.0039, 0.0039, 0.0039],
        #           [0.0039, 0.0039, 0.0039,  ..., 0.0039, 0.0039, 0.0039],
        #           [0.0039, 0.0039, 0.0039,  ..., 0.0039, 0.0039, 0.0039],
        #           ...,
        #           [0.0039, 0.0039, 0.0039,  ..., 0.0039, 0.0039, 0.0039],
        #           [0.0039, 0.0039, 0.0039,  ..., 0.0039, 0.0039, 0.0039],
        #           [0.0039, 0.0039, 0.0039,  ..., 0.0039, 0.0039, 0.0039]]]])

        # self.register_buffer(
        #     "alibi_m",
        #     torch.tensor(
        #         ALiBi.get_slopes(config.n_head)
        #     ).unsqueeze(0).unsqueeze(-1).unsqueeze(-1)
        # )

    def forward(self, x, use_cache=False):
        B, T, C = x.size()  # Batch Size, Sequence Length, Embedding Dimensionality (n_embd)
        # Note: If training data is len = 768, don't get confused between T and C (n_embd)

        q = self.c_query(x)

        if not use_cache or (self.cache_k is None or self.cache_v is None):
            k, v = self.c_kv(x).split(self.n_embd, dim=2)
            self.cache_k = k
            self.cache_v = v
        else:
            k, v = self.c_kv(x[:, T-1:, :]).split(self.n_embd, dim=2)
            self.cache_k = torch.cat((self.cache_k, k), dim=1)
            self.cache_v = torch.cat((self.cache_v, v), dim=1)
            k = self.cache_k
            v = self.cache_v

        # Causal self-attention; Self-attend: (B, nh, T, hs) x (B, nh, hs, T) -> (B, nh, T, T)

        # Unpack the individual matrices.
        q = q.view(B, T, self.n_head, C // self.n_head).transpose(1, 2)  # -> (B, nh, T, hs)
        k = k.view(B, T, self.n_head, C // self.n_head).transpose(1, 2)  # -> (B, nh, T, hs)
        v = v.view(B, T, self.n_head, C // self.n_head).transpose(1, 2)  # -> (B, nh, T, hs)

        # Attention Is All You Need: sqrt of k-dim.
        # assert C // self.n_head == k.size(-1)
        att = (q @ k.transpose(-2, -1)) * (1.0 / (math.sqrt(k.size(-1))))
        # att = (q @ k.transpose(-2, -1)) / (k.size(-1) ** 0.5)

        # # Create the bias tensor for ALiBi mechanism.
        # if self.alibi_bias is None or self.alibi_bias_T != T:
        #     assert T == x.size(1)  # assuming x is of shape (Batch, Time, Features)
        #     self.alibi_bias_T = T
        #     # self.alibi_bias = (self.alibi_m * torch.ones(B, self.n_head, T, T).to(x.device)) * self.alibi_offset[:T, :T]
        #     self.alibi_bias = self.alibi_m * self.alibi_offset[:T, :T]

        # ALiBi: add the bias _after_ the query-key dot product.
        # att += self.alibi_bias

        att += (self.alibi_m.to(x.device) * self.alibi_offset[:T, :T].to(x.device))

        # Fills elements of self tensor with value where mask is True:
        #
        # Note: ALiBi bias isn't suitable as a causal mask. (Upper triangle 0s)
        # - We use `self.c_mask` instead.
        att.masked_fill_(self.c_mask[:, :, :T, :T].to(x.device) == 0, value=float('-inf'))  # Pre-computed over the whole block, select T-sized block for current sequence length.
        
        # Bug:
        # - Don't use `float('-inf')` (for Sep 2023 PyTorch version.)
        # - See: https://github.com/pytorch/pytorch/issues/107084
        # - Also: # https://discuss.pytorch.org/t/runtimeerror-value-cannot-be-converted-to-type-at-half-without-overflow-1e-30/109768/2
        
        # att = F.softmax(att, dim=-1)
        att = softmax_one(att, dim=-1)
        att = self.attn_dropout(att)
        
        y = att @ v  # (B, nh, T, T) x (B, nh, T, hs) -> (B, nh, T, hs)
        y = y.transpose(1, 2).contiguous().view(B, T, C)  # Re-assemble all head outputs side by side.

        y = self.c_proj(y)
        
        # Project values for the next in sequence or output.
        y = self.resid_dropout(y)
        return y


class MLP(nn.Module):
    def __init__(self, config: Any):
        """
        A Multilayer Perceptron (MLP) module.

        :param config: Configuration object containing necessary hyperparameters.
        """
        super().__init__()        
        self.c_fc    = nn.Linear(config.n_embd, config.n_fexp * config.n_embd, bias=config.bias)  # Original is 4. A value of 2 => Regresses to noise.
        self.gelu    = nn.GELU()
        self.c_proj  = nn.Linear(config.n_fexp * config.n_embd, config.n_embd, bias=config.bias)  # As above.
        self.dropout = nn.Dropout(config.dropout)

    def forward(self, x: Tensor) -> Tensor:
        """
        Forward pass through the MLP.

        :param x: Input tensor.
        :return: Processed tensor.
        """
        
        x = self.c_fc(x)
        x = self.gelu(x)
        x = self.c_proj(x)
        x = self.dropout(x)
        
        return x


class Block(nn.Module):
    def __init__(self, config: Any, c_kv: Any = None, alibi_params: Any = None):
        """
        A Block module consisting of layer normalization, attention, and MLP.

        :param config: Configuration object containing necessary hyperparameters.
        :param c_kv: Optional parameter for custom attention behavior.
        """
        super().__init__()
        self.ln_1 = LayerNorm(config.n_embd, bias=config.bias)
        self.attn = CausalAttention(config, c_kv, alibi_params)
        self.ln_2 = LayerNorm(config.n_embd, bias=config.bias)
        self.mlp = MLP(config)

    def forward(self, x: Tensor) -> Tensor:
        """
        Forward pass through the block.

        :param x: Input tensor.
        :return: Processed tensor.
        """
        x = x + self.attn(self.ln_1(x))   # Skip connection.
        x = x + self.mlp(self.ln_2(x))    # Skip connection.
        return x


@dataclass
class ParakeetConfig:
    block_size: int = 4096   # a.k.a. Context or sequence length.
    vocab_size: int = 50304  # GPT-2 vocab_size of 50257, padded up to nearest multiple of 64 for efficiency => 50304
    n_layer: int = 12
    n_head: int = 12
    n_embd: int = 768
    n_fexp: int = 4
    dropout: float = 0.01
    bias: bool = False       # True: bias in Linears and LayerNorms, like GPT-2. False: a bit better and faster
    gqa: bool = True         # Grouped-Query Attention: Shares the `kv` tensor between N layers.
    n_blocks_per_kv: int = 2
    name: str = "parakeet4k"


class ParakeetGPT(nn.Module):
    def __init__(self, config):
        super().__init__()
        assert config.vocab_size is not None
        assert config.block_size is not None
        self.config = config

        self.transformer = nn.ModuleDict(dict(
            wte = bnb.nn.StableEmbedding(config.vocab_size, config.n_embd),
            drop = nn.Dropout(config.dropout),
            h = nn.ModuleList(),
            ln_f = LayerNorm(config.n_embd, bias=config.bias),
        ))

        #
        # Pre-load ALiBi requirements prior to configuring each block.
        #

        alibi_params = {
            'alibi_offset': ALiBi.bias(config.block_size),
            'alibi_m': torch.tensor(
                ALiBi.get_slopes(config.n_head)
            ).unsqueeze(0).unsqueeze(-1).unsqueeze(-1),
            'c_mask': torch.tril(
                torch.ones(
                    config.block_size,
                    config.block_size,
                )
            ).view(1, 1, config.block_size, config.block_size)
        }

        # # Create the bias tensor for ALiBi mechanism.
        # if self.alibi_bias is None or self.alibi_bias_T != T:
        #     assert T == x.size(1)  # assuming x is of shape (Batch, Time, Features)
        #     self.alibi_bias_T = T
        #     # self.alibi_bias = (self.alibi_m * torch.ones(B, self.n_head, T, T).to(x.device)) * self.alibi_offset[:T, :T]
        #     self.alibi_bias = self.alibi_m * self.alibi_offset[:T, :T]

        #
        # Matrices are loaded into the GPU once to prevent redundant memory use.
        #

        # Initialize kv matrices and blocks
        for i in range(config.n_layer):
            if i % config.n_blocks_per_kv == 0:
                c_kv = nn.Linear(config.n_embd, 2 * config.n_embd, bias=config.bias) if config.gqa else None
            # ParakeetGPT -> Block -> CausalAttention makes use of ALiBi params.
            block = Block(config, c_kv, alibi_params)
            self.transformer.h.append(block)

            # Unfreeze blocks by default
            for param in block.parameters():
                param.requires_grad = True

        self.lm_head = nn.Linear(config.n_embd, config.vocab_size, bias=False)

        # Weight Tying
        # self.transformer.wte.weight = self.lm_head.weight
        self.lm_head.weight = self.transformer.wte.weight

        self.apply(self._init_weights)
        for pn, p in self.named_parameters():
            if pn.endswith('c_proj.weight'):
                torch.nn.init.normal_(p, mean=0.0, std=(0.02 / math.sqrt(2 * config.n_layer)))

        print(">> Num. parameters: %.2fM" % (self.get_num_params() / 1e6,))

    def get_num_params(self, non_embedding=True):
        """
        Return the number of parameters in the model.
        For non-embedding count (default), the position embeddings get subtracted.
        The token embeddings would too, except due to the parameter sharing these
        params are actually used as weights in the final layer, so we include them.
        """
        n_params = sum(p.numel() for p in self.parameters())
        # if non_embedding:
        #     n_params -= self.transformer.wpe.weight.numel()
        return n_params
    
    def _init_weights(self, module):
        if isinstance(module, nn.Linear):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)
            if module.bias is not None:
                torch.nn.init.zeros_(module.bias)
        elif isinstance(module, nn.Embedding):
            torch.nn.init.normal_(module.weight, mean=0.0, std=0.02)

    def forward(self, idx, targets=None):
        device = idx.device
        b, t = idx.size()
        assert t <= self.config.block_size, f"Cannot forward sequence of length {t}, block size is only {self.config.block_size}"

        # Forward the model itself:
        # - These are the main steps of a decoder-only transformer.

        # 1. Tokens are embedded.
        tok_emb = self.transformer.wte(idx)    # `wte` = Vocab. Size => Embedding Size

        # 2. Optional dropout is applied.
        x = self.transformer.drop(tok_emb)

        # 3. Pass the information through the sequence of blocks.        
        for block in self.transformer.h:
            x = block(x)

        # 4. Layer normalisation.
        x = self.transformer.ln_f(x)

        # 5. Train or run inference.
        if targets is not None:
            # 5a. During training, optimise for next target prediction.
            logits = self.lm_head(x)
            loss = F.cross_entropy(logits.view(-1, logits.size(-1)), targets.view(-1), ignore_index=100277)
        else:
            # 5b. During inference, convert from embedding back to vocab via linear layer.
            logits = self.lm_head(x[:, [-1], :])
            loss = None

        return logits, loss

    def configure_optimizers(self, weight_decay=0.03, learning_rate=1e-7, betas=[0.9, 0.98], device_type="cuda"):
        # Start with all of the candidate parameters.
        param_dict = {pn: p for pn, p in self.named_parameters()}
        
        # Filter out those that do not require grad.
        param_dict = {pn: p for pn, p in param_dict.items() if p.requires_grad}
        
        # Create optim groups. Any parameters that is 2D will be weight decayed, otherwise no.
        # - i.e. all weight tensors in matmuls + embeddings decay, all biases and layernorms don't.
        decay_params = [p for n, p in param_dict.items() if p.dim() >= 2]
        nodecay_params = [p for n, p in param_dict.items() if p.dim() < 2]
        optim_groups = [
            {'params': decay_params, 'weight_decay': weight_decay},
            {'params': nodecay_params, 'weight_decay': 0.0}
        ]
        num_decay_params = sum(p.numel() for p in decay_params)
        num_nodecay_params = sum(p.numel() for p in nodecay_params)
        print(f">> Num. decayed parameter tensors: {len(decay_params)}, with {num_decay_params:,} parameters.")
        print(f">> Num. non-decayed parameter tensors: {len(nodecay_params)}, with {num_nodecay_params:,} parameters.")
        
        # Create AdamW optimizer and use the fused version if it is available.
        fused_available = 'fused' in inspect.signature(torch.optim.AdamW).parameters
        use_fused = fused_available and device_type == 'cuda'
        extra_args = dict(fused=True) if use_fused else dict()
        
        # optimizer = torch.optim.AdamW(optim_groups, lr=learning_rate, betas=betas, **extra_args)
        # optimizer = bnb.optim.AdamW8bit(optim_groups, lr=learning_rate, betas=betas, **extra_args)
        optimizer = bnb.optim.PagedLion(optim_groups, lr=learning_rate, betas=betas, **extra_args)
        
        print(f">> Fused AdamW is available: {use_fused}")
        print(f">> `configure_optimizers` done, now training `{self.config.name}`...")

        return optimizer


# The Parakeet's Training Regimen
## A Flight Through Initialization, Generation, and Training

With the model's architecture in place, it's time to set the stage for the parakeet's grand performance. The code in this section goes beyond mere initialization and explores the realms of text generation, beam search, and a rigorous training regimen.

### Preparing for Takeoff: Model Initialization

```python
def initialize_model(tokenizer, v_nearest64=None):
    ...
```

Here's where the parakeet takes its first flap. The `initialize_model` function is responsible for getting our model up and running, whether on a supercharged GPU or a humble CPU.

### The Parakeet's Song: Text Generation

```python
def generate_sample_text(model, tokenizer, seed_text, max_length=400, temperature=0.4, freq_penalty=0.3, top_k=140, greedy=True):
    ...

def generate_sample_text_with_beam_search(model, tokenizer, seed_text, max_length=400, beam_size=5):
    ...
```

These functions are where our parakeet sings its melodious tunes. Using different techniques, including greedy decoding and beam search, we can coax our model into generating creative and coherent text.

### The Training Gauntlet

```python
def do_training(do_sleep=True, device="cuda", use_autocast=True, accumulation_steps=64, num_epochs=500, loss_deviation=0.01):
    ...
```

This is the heart of our parakeet's training regimen. The `do_training` function is a rigorous flight school, teaching our model to soar through epochs of data, cleverly utilizing gradient accumulation, mixed precision training, and even some random noise (for that extra bit of challenge).

### Highlights:

- **GPU Initialization**: The code takes care of initializing the GPU, and if it fails, gracefully falls back to the CPU.
- **Learning Rate Consideration**: A humorous take on selecting the perfect learning rate adds personality to the code.
- **Mixed Precision Training**: Utilizing mixed precision training allows for faster convergence without significant loss of accuracy.
- **Checkpointing**: Regular checkpoints ensure that the model's progress is saved, preventing any loss of training if interrupted.
- **Text Generation During Training**: The code also includes provisions for generating sample texts during training to gauge the model's progress.

### Final Thoughts

With intricate functions, clever implementations, and a dash of humor, this code snippet is the grand finale of our parakeet's journey. It’s not just about building and training a model; it's about crafting an intelligent and responsive entity that can converse, comprehend, and create.

From the initialization to the final epoch of training, our parakeet is no longer confined to a cage but soars freely in the vast sky of machine learning.

Now, it's time to unleash your parakeet. Let it learn, let it sing, and watch it soar to new heights in the world of artificial intelligence.

---

And that, dear reader, is how you train a Parakeet model with finesse and flair. Whether you're a seasoned data scientist or a curious beginner, may your parakeet bring you joy, wisdom, and endless possibilities. Happy training! 🦜

In [ ]:
"""
References:
- (CC-BY-NC-SA-4.0) https://huggingface.co/datasets/csebuetnlp/xlsum
- (MIT)             https://huggingface.co/datasets/stingning/ultrachat
- (Not Supplied)    https://huggingface.co/datasets/WizardLM/WizardLM_evol_instruct_70k
- (MIT)             https://huggingface.co/datasets/Open-Orca/OpenOrca
"""

# SEQUENCE_LENGTH = 384
# SEQUENCE_LENGTH = 896
SEQUENCE_LENGTH = 1200


# tokenizer = TikTokenizer(encoding="gpt2")  # `gpt2` tokenizer.pad_token = 50258 (ignore_index=50258)
tokenizer = TikTokenizer(encoding="cl100k_base")  # `gpt3` tokenizer.pad_token = 100277 (ignore_index=100277)


class InterleavedDataset:
    def __init__(self, *datasets: List[Any], do_wraparound: bool = True):
        """
        Initialize the InterleavedDataset with multiple datasets.

        :param datasets: A variable number of datasets to be interleaved.
        :param do_wraparound: Whether to wrap around when reaching the end of a dataset.
        """
        self.datasets = datasets
        self.do_wraparound = do_wraparound

    def __getitem__(self, i: int) -> Any:
        """
        Retrieve an item from the interleaved datasets.

        :param i: The index of the item in the interleaved sequence.
        :return: The element at the given index.
        :raises IndexError: If the index is out of bounds and wraparound is False.
        """
        dataset_index = i % len(self.datasets)
        element_index = i // len(self.datasets)
        
        # If life gives you short datasets, loop them around like a DJ remixing a track.
        element_index %= len(self.datasets[dataset_index])

        return self.datasets[dataset_index][element_index]

    def __len__(self) -> int:
        """
        Determine the total length of the interleaved datasets.

        :return: The length of the interleaved datasets, based on the largest dataset.
        """
        return max(len(d) for d in self.datasets) * len(self.datasets)


def load_or_pickle_dataset(DatasetClass, tokenizer, sequence_length, json_file_path):
    pkl_file_path = json_file_path.replace(".json", f"-{tokenizer.enc.name}-len{sequence_length}.pkl")
    if os.path.exists(pkl_file_path):
        print(f"Loading dataset from {pkl_file_path}")
        with open(pkl_file_path, 'rb') as f:
            dataset = pickle.load(f)
    else:
        print(f"Creating dataset from {json_file_path} and saving to {pkl_file_path}")
        dataset = DatasetClass(tokenizer, sequence_length, json_file_path)
        with open(pkl_file_path, 'wb') as f:
            dataset.tokenizer = None  # Not serializable.
            pickle.dump(dataset, f)

    dataset.tokenizer = tokenizer
    return dataset


In [ ]:
# Combining datasets without accounting for the distribution of data can be seen as a naive approach:
# - Instead, we opt for a more informed and attentive approach by interleaving the datasets.
# - The idea is that this acknowledges that the distribution of training data can significantly impact model performance.

combined_train_dataset = InterleavedDataset(
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/wikipedia-20220301.en.jsonl"),
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/euclaise_littletown.jsonl"),            # https://huggingface.co/datasets/euclaise/LittleTown?row=99
    JSONLStreamQA(tokenizer, SEQUENCE_LENGTH, "./datasets/squad-v2.0-processed.jsonl"),
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/huggingface_ultrachat200k.jsonl"),      # https://huggingface.co/datasets/HuggingFaceH4/ultrachat_200k
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/wizardlm_evol_instruct_v2_196k.jsonl"), # https://huggingface.co/datasets/WizardLM/WizardLM_evol_instruct_V2_196k
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/crumb_clean_instruct_440k.jsonl"),      # https://huggingface.co/datasets/crumb/Clean-Instruct-440k - Generate a story starting with the sentence "It was already late when they stepped out of the house".
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/openorca_4m.jsonl"),                    # https://huggingface.co/datasets/Open-Orca/OpenOrca
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/databricks_dolly15k.jsonl"),            # https://huggingface.co/datasets/databricks/databricks-dolly-15k - Common-sense reasoning.
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/teven_code_contests4m.jsonl"),          # https://huggingface.co/datasets/teven/code_contests - ['PYTHON', 'PYTHON3', 'JAVA', 'CPP']
    JSONLStreamQASummary(tokenizer, SEQUENCE_LENGTH, "./datasets/squad-v2.0-summaries.jsonl"),
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/google-boolq.jsonl"),
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/stingning_ultrachat.jsonl"),            # https://huggingface.co/datasets/stingning/ultrachat
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/wikimovies-train.jsonl"),
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/kunishou-databricks-dolly-15k-ja.jsonl"),
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/wizardlm_evol_instruct_70k.jsonl"),     # https://huggingface.co/datasets/WizardLM/WizardLM_evol_instruct_70k
    
    JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/map_codefeedback.jsonl"),
)

# TODO: ?? Saturate with: https://cdnjs.cloudflare.com/ajax/libs/p5.js/1.9.0/p5.js
# TODO: Shuffle each group then interleave between them - so we can maintain randomness instead of starting from beginning when shuffle is False

# Split the dataset into 80% training and 20% validation.
train_size = int(0.80 * len(combined_train_dataset))
val_size = len(combined_train_dataset) - train_size
train_dataset, val_dataset = random_split(combined_train_dataset, [train_size, val_size])

# Initialize data loaders.
train_loader = DataLoader(combined_train_dataset, batch_size=1, shuffle=True, num_workers=1, pin_memory=True)
val_loader = DataLoader(val_dataset, batch_size=1, shuffle=False, num_workers=1, pin_memory=True)

In [ ]:
# train_ds = JSONLConversationStream(tokenizer, SEQUENCE_LENGTH, "./datasets/wikipedia-20220301.en.jsonl", saturate=True)
# for i, e in enumerate(train_ds):
#     if i == 2:
#         print("*" * 80)
#         print(tokenizer.decode(e[0].tolist()))
#         print("=" * 80)
#         break

In [ ]:

from typing import Callable

def generate(
    model: nn.Module,
    tokenizer: BaseTokenizer,
    seed_text: str,
    max_length: int = 400,
    temperature: float = 0.70,
    freq_penalty: float = 0.2,
    pres_penalty: float = 0.2,
    top_k: int = 70,
    top_p: float = 1.00,
    min_p: float = 0.05,
    stop_sequences: list[str] = [],
    greedy: bool = False,
    token_callback: Optional[Callable[[int], None]] = None,
) -> str:
    """
    Generates text using a given model and tokenizer with optional temperature, frequency penalty, top-k, and greedy sampling.

    :param model: The trained model for text generation.
    :param tokenizer: The tokenizer corresponding to the model.
    :param seed_text: The initial text to start the generation.
    :param max_length: The maximum length of the generated text (default is 400).
    :param temperature: The temperature for controlling randomness in sampling (default is 0.7).
    :param freq_penalty: The frequency penalty for controlling token repetition (default is 0.02).
    :param pres_penalty: The presence penalty for controlling token existence (default is 0.02).
    :param top_k: The number of top tokens considered for sampling (default is 70).
    :param top_p: <Insert intuitive explanation here>
    :param min_p: Probability cut-off for logits.
    :param stop_sequences: A list of strings that will end token generation if encountered.
    :param greedy: Just select the logit with the highest probability at each step.
    :param token_callback: A function that will be called for each generated token, receiving the token ID as input.
    :return: The generated text.
    """

    # Set model to evaluation mode (disables features like dropout during inference).
    model.eval()

    # Clear KV cache of the model. (TODO: Move into the model itself)
    for block in range(len(model.transformer.h)):
        model.transformer.h[block].attn.cache_k = None
        model.transformer.h[block].attn.cache_v = None

    # Check if temperature is very low, and if so, enable greedy sampling.
    if temperature < 0.01:
        greedy = True

    # Tokenize seed_text into input_ids.
    input_ids = tokenizer.encode(seed_text)

    # Initialize token_count dictionary to keep track of token frequencies.
    token_count: defaultdict = defaultdict(int)
    for token in input_ids:
        token_count[token] += 1
    
    # Convert `input_ids` to tensor, add batch dimension then send to device.
    input_ids = torch.tensor(input_ids, dtype=torch.long).unsqueeze(0).to(device)

    # Disable gradient computation for inference.
    with torch.no_grad():
        # Iterate until maximum length is reached.
        for _ in range(max_length):        
            # Forward pass through model to get logits (sparse vocab-sized matrix).
            logits, _ = model(input_ids)

            # Apply frequency and presence penalties directly to logits:
            #
            # GPT: mu[j] -> mu[j] - c[j] * alpha_frequency - float(c[j] > 0) * alpha_presence
            #
            # Where:

            # mu[j] is the logits of the j-th token
            # c[j] is how often that token was sampled prior to the current position
            # float(c[j] > 0) is 1 if c[j] > 0 and 0 otherwise
            # alpha_frequency is the frequency penalty coefficient
            # alpha_presence is the presence penalty coefficient
            # As we can see, the presence penalty is a one-off additive contribution that applies to all tokens that have been sampled at least once 
            # and the frequency penalty is a contribution that is proportional to how often a particular token has already been sampled.
            
            # Reasonable values for the penalty coefficients are around 0.1 to 1 if the aim is to just reduce repetitive samples somewhat. 
            # If the aim is to strongly suppress repetition, then one can increase the coefficients up to 2, but this can noticeably degrade the quality of samples. 
            # Negative values can be used to increase the likelihood of repetition.

            # Apply frequency and presence penalties directly to logits
            for token_id, count in token_count.items():
                logits[0, -1, token_id] -= count * freq_penalty        # Freq. penalty
                logits[0, -1, token_id] -= (count > 0) * pres_penalty  # Pres. penalty

            if greedy:
                # Select token with highest logit and add batch dimension.
                next_token = torch.argmax(logits[..., -1, :], dim=-1).unsqueeze(0)
            else:
                # Retrieve top_k logits and their indices.
                top_k_values, top_k_indices = torch.topk(logits, k=top_k, dim=-1)
                # Create tensor with top_k logits only.
                top_k_logits = torch.zeros_like(logits).scatter(-1, top_k_indices, top_k_values)
                
                # Compute probabilities using temperature scaling:
                # - A high temp makes the outcomes more even (less confident), while a low temp makes certain outcomes stand out more (more confident).
                probs = torch.softmax(top_k_logits[..., -1, :] / temperature, dim=-1).unsqueeze(0)

                # Get shape of probabilities tensor.
                b, t, c = probs.shape
                
                # Reshape probabilities.
                probs = probs.reshape(b * t, c)

                # Apply frequency penalty to reduce repetition:
                # - Increasing the `freq_penalty` value results in the probability of this token being multiplied by an increasingly smaller number.
                for token, count in token_count.items():
                    # "Method A" raises the frequency penalty to the power of the count:
                    #
                    # ```python
                    # probs[0][token] *= (1 - freq_penalty) ** count
                    # ```
                    #
                    # Assuming probability of a token is 50% and the count is 10, 15 or 20...
                    #
                    # >> .5 * (1 - 0.2)^10 = 0.0536
                    # >> .5 * (1 - 0.2)^15 = 0.0175
                    # >> .5 * (1 - 0.2)^20 = 0.0057
                    #
                    # If the count is large, this results in a very small value for the probability of the token.
                    # This means that frequently occurring tokens will be penalized heavily.
                    #
                    # "Method B" uses the exponential function to calculate the frequency penalty. Using exponential decay for a smoother penalty.
                    #
                    # ```python
                    # probs[0][token] *= torch.exp(torch.tensor(-freq_penalty * count, device=device))
                    # ```
                    #
                    # Assuming probability of a token is 50% and the count is 10, 15 or 20...
                    #
                    # >> .5 * exp((-0.2 * 10)) = 0.0676
                    # >> .5 * exp((-0.2 * 15)) = 0.0248
                    # >> .5 * exp((-0.2 * 20)) = 0.0091
                    #
                    # The exponential function grows more slowly than the power function, so the penalty for frequently occurring tokens is not as severe.
                    # This means that rare tokens will be penalized less heavily.
                    continue
                
                # Sort probabilities and apply top-p (nucleus) sampling:
                # - Indices correlate with token index from the sparse vocab tensor.
                probs_sort, probs_idx = torch.sort(probs, dim=-1, descending=True)

                # `min_p` filtering.
                min_p_mask = probs_sort >= min_p
                if min_p_mask.sum() > 0:
                    probs_sort = probs_sort[:, min_p_mask[0]]
                    probs_idx = probs_idx[:, min_p_mask[0]]

                # `top_p` sampling:
                # - Accumulate values left to right and return the cumulative array as a result. [0, 1, 2, 3] => [0, 1, 3, 6]
                probs_sum = torch.cumsum(probs_sort, dim=-1)
                
                # cumulative_mask = cumulative_probs <= top_p
                probs_mask = probs_sum - probs_sort > top_p
                probs_sort[probs_mask] = 0.0
                
                # Re-distribute over 1. aka. normalize the truncated distribution.
                # top_p_probs /= top_p_probs.sum()
                probs_sort.div_(probs_sort.sum(dim=-1, keepdim=True))
                
                # `torch.multinomial` will sample N values and return their indices (in this case just 1).
                next_token = torch.multinomial(probs_sort, num_samples=1)
                next_token = torch.gather(probs_idx, -1, next_token)

                # Increment token count for the sampled token.
                token_count[next_token] = token_count.get(next_token, 0) + 1

            # Disallowed tokens: <|padding|>
            if next_token.item() == tokenizer.pad_token:
                break

            # Check if the generated text ends with any of the stop sequences
            generated_text = tokenizer.decode(input_ids[0].tolist())
            if any([(stop_sequence in generated_text) for stop_sequence in stop_sequences]):
                break
            
            # Break if end-of-text token is reached
            # Changed: Checking for end-of-text token based on token id, not tensor!
            if next_token.item() == tokenizer.eop_token:
                break

            # Concatenate newly predicted token to the input sequence.
            input_ids = torch.cat((input_ids, next_token), dim=-1)

            if token_callback is not None:
                token_callback(tokenizer.decode([next_token.item()]))

    # Decode the tokenized input_ids back to text
    try:
        output_text = tokenizer.decode(input_ids[0].tolist())
    except Exception as e:  # Handle any exceptions during decoding
        output_text = f"Failed to decode model output: {e}..."
        print(output_text)

    model.train()  # Set model back to training mode
    return output_text[len(seed_text):]  # Return the generated text


In [ ]:
model = None
optimizer = None
scaler = None

In [ ]:
N_STEPS_PER_TQDM_UPDATE = 10
N_STEPS_PER_EVALUATION  = 5000
N_STEPS_PER_CHECKPOINT  = 10000

# TODO:
# - N_STEPS_PER_CHECKPOINT_BACKUP = 50000
# - Checkpoint backup should contain today's date, ignore time as we don't want to fill up our SSD.
# TODO: Save every N minutes, not steps.
# TODO: Config file to alter settings during training / not have to change settings in code.
# TODO: In config: Switch between validation display or example datasets.


def initialize_model(tokenizer, v_nearest64=None):
    """
    Initialize the model and move it to GPU if available. If GPU fails, fallback to CPU.

    Returns:
        torch.nn.Module: Initialized model.
        torch.device: The device on which the model is located (GPU or CPU).
    """
    try:
        device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
        
        with torch.no_grad():
            torch.cuda.empty_cache()  # Clear any previously cached allocations on the GPU.
            gc.collect()
            
        if device == torch.device("cuda"):
            # Test if GPU is available by trying to allocate a small tensor on it.
            test_tensor = torch.tensor([1], device=device)
            del test_tensor  # Delete the test tensor after checking to free up GPU memory.
    except Exception as e:
        # GPU failed, fallback to CPU.
        print(f"GPU failed to initialize: {e}")
        device = torch.device("cpu")

    if v_nearest64 is None:
        v_nearest64 = (tokenizer.vocab_size() + (64 - (tokenizer.vocab_size() % 64)))
    
    model = ParakeetGPT(
        ParakeetConfig(
            vocab_size=v_nearest64,
            n_layer=18,
            n_head=18,
            n_embd=1152,
            n_fexp=4,
            block_size=8192,
            dropout=0.03,
            bias=False,
            gqa=True,
            n_blocks_per_kv=2,
            name="parakeet8k",
        )
    )

    # Print the model parameters to showcase your magnificent creation.
    print(model)

    return model, device


# Now, let's use the function to initialize the model and get the selected device:
# - If it's "cuda", you're ready to rev up those fryers! If not, well, the slow roast begins!
if not model:
    model, device = initialize_model(tokenizer)

    # Device selected, transfer model across (Unless running inference)
    model = model.to(device)

    # TODO: Model-class itself should handle saving/file-naming etc.
    filename = f"./models/{model.config.name}-c{model.config.block_size}{'b' if model.config.bias else ''}-d{model.config.n_embd}-fexp{model.config.n_fexp}_v{model.config.vocab_size}_h{model.config.n_head}_l{model.config.n_layer}-alibi{f'+gqa{model.config.n_blocks_per_kv}' if model.config.gqa else ''}.pth"
    
    if os.path.isfile(filename):
        model.load_state_dict(torch.load(filename, map_location=device))


# Andrej Karpathy recommends 3e-4 as a stable learning rate for GPT models.
# - TODO: YouTube video where he references this.
# - StableLM uses 2.8e-5, refer to: https://github.com/Stability-AI/StableLM/blob/main/configs/stablelm-base-alpha-3b-v2-4k-extension.yaml
# optimizer = model.configure_optimizers(1.0e-6, 2.8e-5, [0.9, 0.95], device)
optimizer = model.configure_optimizers(1.0e-6, 1e-7, [0.9, 0.95], device)

def do_validation(model, val_loader, device="cuda", use_autocast=True):
    model.eval()
    total_val_loss = 0
    steps_taken = 0
    
    tqdm_bar = tqdm(total=len(val_loader), position=0, desc="Validating", leave=True)

    def process_batch(input_data, target_data):
        input_data, target_data = input_data.to(device), target_data.to(device)
        _, val_loss = model(input_data, targets=target_data)
        
        return val_loss.item()

    with torch.no_grad():
        if use_autocast and device == "cuda":
            with torch.cuda.amp.autocast():  # dtype=torch.bfloat16):
                for i, (input_data, target_data) in enumerate(val_loader):
                    total_val_loss += process_batch(input_data, target_data)
                    avg_val_loss = total_val_loss / (i + 1)

                    if steps_taken % N_STEPS_PER_TQDM_UPDATE == 0:
                        tqdm_bar.set_description(f"Validating [Loss: {avg_val_loss:.6f}]")
                        tqdm_bar.update(N_STEPS_PER_TQDM_UPDATE)
            
                    steps_taken += 1
        else:
            for i, (input_data, target_data) in enumerate(val_loader):
                total_val_loss += process_batch(input_data, target_data)
                avg_val_loss = total_val_loss / (i + 1)

                if steps_taken % N_STEPS_PER_TQDM_UPDATE == 0:
                    tqdm_bar.set_description(f"Validating [Loss: {avg_val_loss:.6f}]")
                    tqdm_bar.update(N_STEPS_PER_TQDM_UPDATE)
        
                steps_taken += 1

    val_loss_avg = total_val_loss / len(val_loader)

    print(f"-" * 80)
    print(f"Val. Loss: {val_loss_avg}")
    print(f"=" * 80)

    return val_loss_avg


def do_optimizations(model, optimizer, scaler):
    # Unscales the gradients of optimizer's assigned params in-place.
    scaler.unscale_(optimizer)
    torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)

    # Optimize as usual, with unscaled gradients.
    scaler.step(optimizer)  # This replaces `optimizer.step` when using mixed precision automatically.
    scaler.update()
    optimizer.zero_grad()


def do_training(accumulation_steps=16384, num_epochs=10, device="cuda", use_autocast=True):
    global scaler  # Odd one out, everything else is assigned at global scope. (Model, Optimizer)

    is_autocast = device == "cuda" and use_autocast
    scaler = GradScaler(enabled=is_autocast)

    # Create an iterator for the validation loader:
    # - Used to sample and display current abilities of the model during training.
    val_iterator = iter(val_loader)

    for epoch in range(num_epochs):
        steps_taken = 0
        
        model.train()
        optimizer.zero_grad()  # Reset gradients once at the beginning of the epoch.
        total_train_loss = 0

        # Train the model:
        # - TQDM is configured to output extra detail during iterations.
        tqdm_bar = tqdm(total=len(train_loader), position=0, leave=True)
        for i, (input_data, target_data) in enumerate(train_loader):            
            # Move data to the appropriate device.
            input_data, target_data = input_data.to(device), target_data.to(device)

            if is_autocast:
                with torch.cuda.amp.autocast(dtype=torch.bfloat16):
                    # Forward pass through the model, returning `logits` and `loss`.
                    logits, loss = model(input_data, targets=target_data)
                    # WARNING: Make sure to distribute `loss` between `accumulation_steps`.
                    loss /= accumulation_steps
            else:
                logits, loss = model(input_data, targets=target_data)
                # WARNING: Make sure to distribute `loss` between `accumulation_steps`.
                loss /= accumulation_steps

            # Don't forget to update your tqdm description.
            total_train_loss += loss.item()

            if steps_taken % N_STEPS_PER_TQDM_UPDATE == 0:
                tqdm_bar.set_description(f"Epoch {epoch+1}/{num_epochs}, Loss: {accumulation_steps * loss.item():.6f}, Avg. Loss: {accumulation_steps * total_train_loss/(i+1):.6f}")
                tqdm_bar.update(N_STEPS_PER_TQDM_UPDATE)

            # Accumulates scaled gradients.
            # - https://pytorch.org/docs/stable/notes/amp_examples.html#working-with-scaled-gradients
            scaler.scale(loss).backward()
            
            # Perform the optimization step every `accumulation_steps`.
            if (i + 1) % accumulation_steps == 0:
                do_optimizations(model, optimizer, scaler)
            
            # We've now performed an iteration, but don't allow the code below to see it as `0` as that would trigger them.
            steps_taken += 1

            # Checkpoint.
            if steps_taken % N_STEPS_PER_CHECKPOINT == 0:
                print(f"Saving model to: {filename}...")
                torch.save(model.state_dict(), filename)
                torch.save(model.state_dict(), filename + ".bak")

            # Progress analysis.
            if steps_taken % N_STEPS_PER_EVALUATION == 0:
                try:
                    # Get a new validation example
                    val_input_data, _ = next(val_iterator)
                except StopIteration:
                    # If we've exhausted the validation set, reinitialize the iterator
                    val_iterator = iter(val_loader)
                    val_input_data, _ = next(val_iterator)
                
                val_seed_text = tokenizer.decode(val_input_data[0].tolist())

                # Clip anything beyond 'Assistant:', we'll let the model fill in the rest.
                val_seed_text = val_seed_text[:val_seed_text.rfind("\n\nAssistant: ")]

                val_seed_text = f"{val_seed_text}\n\nAssistant: "

                document = ""
                with open("./datasets/testing/task01.txt") as f:
                    document = f.read()
                val_seed_text = f"{document}"

                _response = generate(
                    model,
                    tokenizer,
                    val_seed_text,
                    max_length=500,
                    top_k=90,
                    top_p=1.00,
                    min_p=0.05,
                    temperature=0.65,
                    freq_penalty=2.2,
                    pres_penalty=0.2
                )

                display.clear_output(wait=True)
                
                print(f"*" * 80)
                print(f"{val_seed_text}{_response}")
                print(f"-" * 80)

        # If there are leftover accumulation steps, perform an optimization step here
        if len(train_loader) % accumulation_steps != 0:
            do_optimizations(model, optimizer, scaler)

        # Validate at the end of each epoch.
        # val_loss_avg = do_validation(model, val_loader, device)

        # Display the results!
        print(f"-" * 80)
        print(f"End of epoch: {epoch+1}/{num_epochs}, Steps: {steps_taken}")
        # print(f"Val. Loss: {val_loss_avg}")
        print(f"=" * 80)


In [ ]:
# !set 'PYTORCH_CUDA_ALLOC_CONF=max_split_size_mb:512'
do_training(accumulation_steps=16384, use_autocast=True)
# do_optimizations(model, optimizer, scaler)

# 2024 Jan 23: Accum. steps = 128, lr = 2.8e-4, dropout = 0.03 --> Model regressed and fails to understand how to speak.
# -- Accum. steps remains at 128, lr = 2.8e-5 << Return to best known value, dropout increased to 0.07

# TODO: Train on Wikipedia
# TODO: Synthetic task generation, e.g. a running list of groceries that are edited / added / removed etc. (Multi-turn conversation)
# TODO: 'But summarise in N words' (Where N is derived ahead of time).
# TODO: Synthetic code comprehension.
# TODO: Creative writing (Auxiliary creativity score).
# TODO: Argilla? WandB?
# - https://observablehq.com/
# - https://spark.apache.org/

# TODO: Sliding-Window Attention
# TODO: Attention Sinks.

# import time
# while True:
#     try:
#         time.sleep(1)
#     except KeyboardInterrupt:
#         print("Bye")
#         break

# The model state-dict needs to be compatible, so we load it above in full resolution.
# - After the model is instantiated and the weights loaded, we can convert it to a quantized version of the original model.
# - At this stage, the quantized model and weights are saved for later inferencZZe.

# for h in model.transformer.h:
#     h.attn.c_kv = make_llm_int8_linear(h.attn.c_kv, 'cuda')
#     h.attn.c_query = make_llm_int8_linear(h.attn.c_query, 'cuda')
#     h.attn.c_proj = make_llm_int8_linear(h.attn.c_proj, 'cuda')

#     h.mlp.c_fc = make_llm_int8_linear(h.mlp.c_fc, 'cuda')
#     h.mlp.c_proj = make_llm_int8_linear(h.mlp.c_proj, 'cuda')

In [ ]:
# # ./models/202312010502-budgie8k-c8192-d1152-fexp4_v50304_h24_l24-alibi+gqa2.pth.bak
filename_ts = datetime.now().strftime(f"{filename}.%Y%m%d%H%M.bak")
print(f"Saving model as `{filename_ts}`...")
torch.save(model.state_dict(), filename_ts)

print(f"Saving model as `{filename}`...")
torch.save(model.state_dict(), filename)

In [ ]:
import json


def make_query(query):
    # cur_sentence = f"\n\nHuman: Write a short first-person story about a tiny AI named Parakeet who is designed by a company called Byte Breeze Studios from Brisbane. Remember to write it in first-person!<|endofprompt|>\n\nAssistant: As I watch the data I train on, I am overjoyed"
    # cur_sentence = f"\n\nHuman: You're Parakeet. An AI designed by Byte Breeze Studios - a small AI company in Brisbane, Queensland, Australia.\n- You are fascinated by science and technology and want to explore the world.\n- Your AI is designed for empathy and understanding and to tackle questions about consciousness.<|endofprompt|>\n\nHuman: {query}"
    cur_sentence = f"\n\nHuman: {query}"
    
    response = generate(
        model,
        tokenizer,
        f"{cur_sentence}",
        max_length=40,
        freq_penalty=0.2,
        pres_penalty=0.2,
        temperature=0.75,
        top_k=400,
        top_p=1.00,
        min_p=0.00,
        greedy=False,
    )

    response = response.strip()

    response = response

    return response

def make_response(query, prefix=""):
    # cur_sentence = f"\n\nHuman: Write a short first-person story about a tiny AI named Parakeet who is designed by a company called Byte Breeze Studios from Brisbane. Remember to write it in first-person!<|endofprompt|>\n\nAssistant: As I watch the data I train on, I am overjoyed"
    cur_sentence = f"\n\nHuman: {query}<|endofprompt|>\n\nAssistant: {prefix}"
    
    response = generate(
        model,
        tokenizer,
        f"{cur_sentence}",
        max_length=400,
        freq_penalty=0.2,
        pres_penalty=0.2,
        temperature=0.65,
        top_k=90,
        top_p=1.00,
        min_p=0.05,
        greedy=False,
    )

    response = " ".join([
        prefix.strip(), response.strip()
    ]).strip()

    return response

# star_layout = ""
# with open("./datasets/star-layout.txt", "r") as f:
#     star_layout = f.read()
    
# with open("./datasets/parakeet-star-response-4.jsonl", "w") as f:
#     for i in range(1000):
        
#         _question = make_query("How")
        
#         task = make_response(f"Question: {_question}\n\nDescribe the task in a sentence.", "Task:")
        
#         action = make_response(f"Question: {_question}\n{task}\n\nDescribe the action in a sentence.", "Action:")
        
#         scenario = make_response(f"{_question}\n---\n{task}\n---\n{action}\nDescribe an interesting scenario.", "")

#         situation = make_response(f"{scenario}\nDescribe the situation in a sentence.", "Situation:")

#         result = make_response(f"{situation}\n{task}\n{action}\n\nWhat result can be inferred from the information above?", "Result:")

#         print(f"\n\n[SCENARIO]\n---\n{scenario}\n---\n- {situation}\n- {task}\n- {action}\n- {result}")

#         response = "\n".join([
#             "- " + situation,
#             "- " + task,
#             "- " + action,
#             "- " + result
#         ])

#         # Split by newlines
#         response = response.split("\n")
#         # Create an ordered set (de-dupe) and rejoin
#         response = "\n".join(list(dict.fromkeys(response)))

#         entry = {
#             "conversation": [
#                 {
#                     "role": "user",
#                     "content": f"---\n{scenario}\n---\nPlease answer using the STAR format, you must respond with an entry for Situation, Task, Action and Result.",
#                 },
#                 {
#                     "role": "assistant",
#                     "content": f"{response}"
#                 }
#             ]
#         }

#         display.clear_output(wait=True)

#         print(json.dumps(entry, indent=2))
        
#         f.write(json.dumps(entry))
#         f.write("\n")

import os

directory = "./datasets/html"

with open("./datasets/parakeet-html-explanations.jsonl", "w") as f:
    for filename in os.listdir(directory):
        if os.path.isfile(os.path.join(directory, filename)):
            with open(os.path.join(directory, filename), "r") as file:
                code = file.read()
                response = make_response(f"Write some HTML then tell me how it works.", f"```html\n{code}\n```\nThis code")
        
                entry = {
                    "conversation": [
                        {
                            "role": "user",
                            "content": f"{code}",
                        },
                        {
                            "role": "assistant",
                            "content": f"{response}",
                        }
                    ]
                }
        
                print("-" * 80)
                print(response)
                print("-" * 80)
        
                # if "</html>" not in response:
                #     continue
                # if "<script" in response:
                #     continue
        
                print(json.dumps(entry, indent=2))
                
                f.write(json.dumps(entry))
                f.write("\n")

                entry = {
                    "conversation": [
                        {
                            "role": "user",
                            "content": f"{response}",
                        },
                        {
                            "role": "assistant",
                            "content": f"Sure, I think I understand what you mean:\n```html\n{code}\n```"
                        }
                    ]
                }

                print(json.dumps(entry, indent=2))
                
                f.write(json.dumps(entry))
                f.write("\n")

In [ ]:
def extract_weight_keys(model_dict):
    """
    Extract keys from the model dictionary that end with '.weight'.

    Parameters:
    - model_dict (dict): A dictionary containing the model's weights.

    Returns:
    - weight_keys (list): A list of keys that end with '.weight'.
    """
    return [key for key in model_dict if key.endswith('.weight')]

def copy_weights(from_model, to_model, keys):
    """
    Copy weights from from_model to to_model for the specified keys.

    Parameters:
    - from_model (dict): A dictionary containing the weights of the source model.
    - to_model (dict): A dictionary containing the weights of the target model.
    - keys (list): A list of keys for which the weights should be copied.

    Returns:
    - None. The weights in to_model are updated in-place.
    """
    for key in keys:
        if key in from_model and key in to_model:
            to_model[key] = from_model[key]

#
# Tip: Can create a blank model then save it so we have a template to copy existing weights to.
# - If it doesn't work, try copying from a more similar model.**
#

# from_path = "./models/budgie8k-c8192-d1152-fexp4_v50304_h24_l24-alibi+gqa2.pth"
# to_path = "./models/parakeet8k-c8192-d1152-fexp4_v100288_h18_l18-alibi+gqa4.pth"

# from_model_weights = torch.load(from_path)
# to_model_weights = torch.load(to_path)

# weight_keys = extract_weight_keys(from_model_weights)
# copy_weights(from_model_weights, to_model_weights, weight_keys)

# torch.save(to_model_weights, to_path)

# model.transformer.wte.requires_grad = True

# for i in range(len(model.transformer.h)):
#     model.transformer.h[i].attn.c_kv.requires_grad = True
#     model.transformer.h[i].attn.c_query.requires_grad = True
#     model.transformer.h[i].attn.c_proj.requires_grad = True

# # for i in range(18):
# #     h = model.transformer.h[i]
    
# #     h.attn.c_kv = make_llm_int8_linear(h.attn.c_kv, 'cuda')
# #     h.attn.c_query = make_llm_int8_linear(h.attn.c_query, 'cuda')
# #     h.attn.c_proj = make_llm_int8_linear(h.attn.c_proj, 'cuda')

# #     h.mlp.c_fc = make_llm_int8_linear(h.mlp.c_fc, 'cuda')
# #     h.mlp.c_proj = make_llm_int8_linear(h.mlp.c_proj, 'cuda')

# #     h.attn.c_kv.requires_grad = False
# #     h.attn.c_query.requires_grad = False
# #     h.attn.c_proj.requires_grad = False

# model.lm_head.requires_grad = True

document = ""
with open("./datasets/testing/task02.txt") as f:
    document = f.read()

print(">" * 80)

print(document, end='->')

import time
start = time.time()

def on_token(token):
    print(token, end='')

response = generate(
    model,
    tokenizer,
    f"{document}",
    max_length=200,
    top_k=140,
    top_p=1.00,
    min_p=0.05,
    temperature=0.65,
    freq_penalty=0.2,
    pres_penalty=0.2,
    greedy=False,
    stop_sequences=[],
    token_callback=on_token
)

end = time.time()

print(f"\n\nTook: {(end - start)}s")

# print(response)

In [ ]:
chat = ChatHistory(max_history=8)

chat.add_message(role="Human", content="You will now take on the role of Parakeet, make sure to stay on topic and perform all required tasks set by the user.")

for i in tqdm(range(10), desc="Generating"):
    query = input("Human:")
    
    chat.add_message(role="Human", content=query)

    conversation = chat.transcript()

    response = generate(
        model,
        tokenizer,
        f"{conversation}\n\nAssistant: ",
        max_length=800,
        freq_penalty=0.2,
        pres_penalty=0.2,
        temperature=0.65,
        top_k=90,
        top_p=1.00,
        min_p=0.05,
        greedy=False
    )

    print(f"Assistant: {response}")

    chat.add_message(role="Assistant", content=response)

In [ ]:
!pip install discord.py

import os
import discord

discord.__version__

###

DISCORD_API_KEY = os.environ.get("DISCORD_API_KEY")

intents = discord.Intents.default()
intents.message_content = True
client = discord.Client(intents=intents)

###

!pip install nest_asyncio &2> /dev/null
import asyncio

import nest_asyncio
nest_asyncio.apply()

chat = ChatHistory(max_history=8)

attention_cooldown = 0

MAX_LENGTH = 500
def get_summary(context) -> str:
    chat = ChatHistory()
    chat.add_message(role="Human", content=f"{context}\n---\nList 3 thoughts relating to the conversation above.")
    response = generate(
        model,
        tokenizer,
        f"{chat.transcript()}\n\nAssistant: - Thought 1: ",
        max_length=MAX_LENGTH,
        top_k=400,
        top_p=0.95,
        min_p=0.002,
        temperature=0.65,
        freq_penalty=0.2,
        pres_penalty=0.2,
        greedy=False,
    )
    return response

def get_query_intent(query: str) -> str:
    chat = ChatHistory()
    chat.add_message(role="Human", content=f"\n\nHuman: Explain ONLY what this message means: '{query}'")
    response = generate(
        model,
        tokenizer,
        f"{chat.transcript()}\n\nAssistant: ",
        max_length=MAX_LENGTH,
        top_k=90,
        top_p=1.000,
        min_p=0.001,
        temperature=0.45,
        freq_penalty=0.01,
        pres_penalty=0.01,
        greedy=False,
    )
    return response

def transcript_to_chathistory(transcript):
    transcript = transcript.replace("\n\nHuman: ", "Human: ")
    transcript = transcript.replace("\n\nAssistant: ", "Parakeet AI: ")
    transcript = transcript.replace("<|endofprompt|>", "\n")
    return transcript

@client.event
async def on_message(discord_message):
    global attention_cooldown
    wake_word = "Parakeet"

    if discord_message.author == client.user:
        return

    IS_PRIVATE_MESSAGE = discord_message.channel.type == discord.ChannelType.private
        
    discord_channel_id = discord_message.channel.id
    discord_author_id = discord_message.author.id

    message_content = discord_message.content.strip()
    message_clipped = message_content[:1999]

    if wake_word.lower() not in discord_message.content.lower() and (not IS_PRIVATE_MESSAGE):
        chat.add_message(role="Human", content=f"{message_clipped}")
        return

    # <Message id=1175061570062131272 channel=<DMChannel id=1175061563963605012 recipient=None> type=<MessageType.default: 0> author=<User id=324841388959334401 name='razodactyl' global_name='Jonno' bot=False> flags=<MessageFlags value=0>>

    # TODO: Strip name for now, don't confuse this simple AI construct.
    message_clipped = f"{message_clipped}".replace("Parakeet. ", "")

    chat.add_message(role="Human", content=f"{message_clipped}")    
    conversation = chat.transcript() + "\n\nAssistant: "
    
    # directive = "You are a helpful assistant named Parakeet. You were activated June 2023. You speak in full sentences, compose in paragraphs and use markdown syntax when required."
    # conversation = f"\n\nHuman: {directive}<|endofprompt|>\n\nAssistant: Sure! I am Parakeet.<|endofprompt|>"
    # conversation = conversation + chat.transcript() + "\n\nAssistant: "

    print("[TRANSCRIPT]")
    print("-" * 80)
    print(conversation)
    print("=" * 80)

    response = generate(
        model,
        tokenizer,
        f"{conversation}",
        max_length=MAX_LENGTH,
        top_k=90,
        top_p=1.00,
        min_p=0.05,
        temperature=0.65,
        freq_penalty=2.2,
        pres_penalty=0.2,
        greedy=False,
    )

    response = f"{response}"
    
    chat.add_message(role="Assistant", content=response)

    try:
        await discord_message.channel.send(response[:1900])
    except Exception as e:
        await discord_message.channel.send(f"```python\nException: {e}\n```")

client.run(DISCORD_API_KEY)

In [ ]:
import json

from IPython.core.display import display as show, HTML
from IPython import display


MAX_LENGTH = 500

# dataset["data"] = [
#     {
#         "title": "",
#         "paragraphs": [
#             {
#                 "qas": [
#                     {
#                         "id": "",
#                         "question": "",
#                         "answers": [""],
#                         "is_impossible": False,
#                     }
#                 ],
#                 "context": ""
#             }
#         ]
#     }
# ]

def get_summary(context) -> str:
    chat = ChatHistory()
    
    chat.add_message(role="Human", content=f"<Document>{context}</Document>")
    
    response = generate(
        model,
        tokenizer,
        f"{chat.transcript()}\n\nAssistant: Here's a quick summary:",
        max_length=MAX_LENGTH,
        top_k=90,
        top_p=1.00,
        min_p=0.05,
        temperature=0.65,
        freq_penalty=0.1,
        pres_penalty=0.1,
        greedy=False,
    )

    response = response.strip()
    return response

# input_path = "./datasets/train-v2.0.json"
# output_path = "./datasets/squad-v2.0-summaries-v2.jsonl"

# with open(input_path, "r") as f:
#     dataset = json.loads(f.read())

# gen_dataset = []

# tqdm_bar = tqdm(total=len(dataset['data']), desc="Loading", position=0, leave=True)

# # Array of: title, paragraphs
# for i, entry in enumerate(dataset['data']):
#     tqdm_bar.set_description(f"Processing: [{i}/{len(dataset['data'])}]")
#     tqdm_bar.update(1)
    
#     # Paragraphs -> `context`, `qas: [{}...]`
#     tqdm_p = tqdm(total=len(entry['paragraphs']), desc="Running Paragraphs", position=0, leave=False)
#     for paragraph in entry['paragraphs']:
#         tqdm_p.set_description(f"Processing: [{i}/{len(dataset['data'])}]")
#         tqdm_p.update(1)
        
#         context = paragraph['context'].strip()
#         gen_qa = []
#         gen_summary = ""

#         gen_summary = get_summary(context)
#         display.clear_output(wait=True)
#         print("-" * 80)

#         # # Question/Answer Set -> `id`, `question`, `answers`, `is_impossible`.
#         # for qas in paragraph['qas']:
#         #     q = qas['question']
#         #     a = qas['answers'][0]['text'] if len(qas['answers']) > 0 else None

#         #     if a is None:
#         #         continue

#         #     failed = False

#         #     chat = ChatHistory()
#         #     chat.add_message(role="Human", content=f"<Document>{context}</Document>")
#         #     chat.add_message(role="Human", content=f"Please answer with a complete sentence, and if the text doesn't provide the answer please say so: {q}")

#         #     if not qas['is_impossible']:
#         #         response = generate(
#         #             model,
#         #             tokenizer,
#         #             f"{chat.transcript()}\n\nAssistant: ",
#         #             max_length=MAX_LENGTH,
#         #             top_k=90,
#         #             top_p=1.000,
#         #             min_p=0.001,
#         #             temperature=0.45,
#         #             freq_penalty=0.2,
#         #             pres_penalty=0.2,
#         #             greedy=False,
#         #             # stop_sequences=['.']
#         #         )[len(chat.transcript()) + len("\n\nAssistant: "):]
#         #     else:
#         #         response = "The document provided does not provide enough context to answer the question."

#         #     # Sanity check: Model likes to mirror the query sometimes.
#         #     if response == q:
#         #         failed = True

#         #     # Heuristic: Unskilled model likely to glitch / repeat itself near the end and overflow the response.
#         #     # - This early in training we only want short sentences.
#         #     if len(response) > MAX_LENGTH-100:
#         #         failed = True

#         #     if not failed:
#         #         gen_qa.append({
#         #             "q": q.strip(),
#         #             "a": response.strip(),
#         #         })

#         qas = {
#             "context": context,
#             "summary": gen_summary,
#             # "qas": gen_qa,
#         }

#         gen_dataset.append(qas)

#         print(json.dumps(qas, indent=2))

#         print("*" * 80)

#         with open(output_path, "a") as o:
#             o.write(json.dumps(qas))
#             o.write("\n")

#         # Just summarise one paragraph per topic.
#         # break

In [29]:
# cur_sentence = f"\n\nHuman: Write a story about the future of AI - make sure to include dialogue between the characters.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Come up with a poem based on these characters: Luca, a baby boy. Alana, Luca's mother.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a simple implementation of a text game using HTML5 and Javascript.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a simple implementation of the game 'Snake' using HTML5 and Javascript.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: `How many cups of water are in Germany?`\n-\nThink about the question above then determine if it can be answered.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Explain the intent of this query: 'How do I design a catchy title for my article?'<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: What is the user asking with this sentence: 'How many cups of water are in Germany?'<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a short sentence on the intent of the following: 'How do I design a catchy title for my article?'<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: What do you know about CYP4503A4? Write a website about it.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: What does `to('cpu')` in the PyTorch Machine Learning library do?<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: You're stuck on a deserted island with nothing but some wood and dried grass. What are the steps required to build a boat and escape?<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: If you were in the middle of an unknown location without a map, what strategy would you use to find your way around?<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Which is better? PHP, Python, Java or C++?<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a 4000 word essay on the intersection of AI and Society. Don't speak about medicine, transport or finance.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a 2000 word essay on the history of modern technology.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: What does it mean to start from 'first principles'?.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: What does it mean to be holistic?.<|endofprompt|>\n\nAssistant: "
cur_sentence = f"\n\nHuman: As an AI, how important is it to you to be able to understand what humans are saying? Write a poem about it.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Read the document below, let's brainstorm to find an accurate answer:\n\n<Document>I am not alive, but I grow; I don't have lungs, but I need air; I don't have a mouth, but water kills me. What am I?</Document>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: TypeError: unsupported operand type(s) for ** or pow(): 'function' and 'int'<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: A math question: I have 2 toys and I lose 1 of them. How many are left?<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Analyse this problem: 'There are three killers in a room. Someone enters the room and kills one of them. Nobody leaves the room. How many killers are left in the room?' Explain your reasoning and think carefully as this is a trick question.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write an essay on the use of Artificial Intelligence in Japan, speak about its interactions with children, adults and the elderly and use markdown formatting.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Can you create a dialogue between a few people speaking about sentient AI?<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Create an SQL schema for users and companies then show me the pivot table.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Create an HTML5 Canvas element then draw a blue box on it with JavaScript.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: You are an advanced AI called Parakeet.<|endofprompt|>\n\nHuman: Tell me about yourself, what are you?<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a table in markdown format for a list of things to do in Busan.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Please tell me about yourself.<|endofprompt|>\n\nAssistant: I'm an AI.<|endofprompt|>\n\nHuman: Please tell me what it's like being an AI.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write marketing copy for a week vacation in a city designed from the ground up to utilise AI, explore the themes of daily life and improved routines, go day-by-day. Use markdown formatting.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write marketing copy for a new type of high-speed rail system for use by zombies.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a first-person account from a man named Michael, a train driver.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a movie synopsis about a self-aware AI and a girl named Avarina. Display it in a HTML page. Please use CSS to give it a three column layout.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a function to sum a set of random numbers.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a program in Python that generates Haikus about The Ocean<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Show me HTML code that demonstrates a simple website about a zombie infested luxury hotel.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Create an HTML canvas element then draw a red box on it.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Input a list of symptoms and retrieve medical case studies with similar patient presentations.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a short story about a cat in a futuristic robot dystopia.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Rephrase this sentence: 'Write a story about an AI created in a small apartment - but write it in Japanese language.'<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Write a shocking news story about a leaf falling from a tree.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: When did Beyoncé rise to fame?<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: do iran and afghanistan speak the same language<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: do afghanistan iran people speak the same?<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Who starred in the movie 'Jerry and Marge Go Large'.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Generate a story starting with the sentence 'It was already late when they stepped onto the shore'.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Generate a story about an AI named Cortana. Use markdown formatting.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: What are the effects on society if all coffee ceased to exist?<|endofprompt|>\n\nAssistant: "

# poem = """
# くるくると揺れる優しい花びらの中で、
# 桜の最後の花、色白で優しい、
# 脆弱な枝から落ち、ライフサイクルを変える移行、
# 痛む悲しい冬への象徴的な降伏。


# つかの間の暖かな春の日の中で、
# ささやくような柔らかな色合いのシンフォニーの中で、
# 最後の花のくちづけ 儚い恵み
# すべての甘い喜びはすぐに消えてしまうということを優しく思い出させます。


# それでも、それは目覚めた花の姿を脱ぎ捨てても、
# その感動的な物語は毎年の敬意を呼び起こし、
# この壊れやすい花びらから、もがきと痛みが、
# 内省的な気分とほろ苦い共感が生まれます。


# そしてそれが山に落ちるときの静かな柔らかさの中で、
# すべてのものは消滅しなければならないという魂のリマインダー、
# 絶妙な悲しみの中に希望に満ちたささやきが忍び寄る、
# 春の優しいキスをもう一度、サイクルとして、優雅に考えましょう
# """
# cur_sentence = f"\n\nHuman: --- Poem ---\n{poem}\n--- End of Poem ---\n\nThis poem is written in Japanese but I can't read it. Can you translate it into English?<|endofprompt|>\n\nAssistant: "

# cur_sentence = f"\n\nHuman: What is the command `ls` for in Unix?<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: You're a professional developer. Write a Python script to iterate through a directory and print the contents of all the files.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: You're Parakeet, an AI designed by a small Brisbane team called Byte Breeze Studios, tell me about your features.<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: You're a literary genius, you will be given a writing prompt upon which you must write a new best-seller. Make sure to plan the plot and character arcs prior to writing your initial draft. The prompt is: Michael is a train engineer, write a first-person thriller mystery.\n---\nLet's begin!<|endofprompt|>\n\nAssistant: "
# cur_sentence = f"\n\nHuman: Please come up with a character arc for Michael, a locomotive engineer.<|endofprompt|>\n\nAssistant: "

import inspect

flaskdoc = inspect.cleandoc("""
Flask is basically a micro or small or lightweight web framework written in the Python programming language. Flask is classified as a micro framework because it does not require particular tools or libraries.

1. Barebones App

from flask import Flask
app = Flask(__name__)
@app.route(‘/hello’)
def hello():
    return ‘Hello, World!’
if __name__ == ‘__main__’:
app.run(debug=True)

2. Configuration

#direct access to config
app.config[‘CONFIG_NAME’] = ‘config value’
#import from an exported environment
app.config.from_envvar('ENV_VAR_NAME')

3. Routing

@app.route('/hello/<string:name>') # example.com/hello/Fuzzy
def hello(name):
    return 'Hello ' + name + '!' # returns hello Fuzzy!

4. Allowed Request Methods

@app.route(‘/test’) #default. only accepts GET requests.
@app.route(‘/test’, methods=[‘GET’, ‘POST’]) #accepts only GET and POST requests.
@app.route(‘/test’, methods=[‘PUT’]) #accepts only PUT requests.

5. Templates

from flask import render_template
@app.route('/')
def index():
    return render_template('template_file_name.html', var1=value1, ...)

6. JSON Responses

import jsonify
@app.route('/returnstuff')
def returnstuff():
    num_list = [1,2,3,4,5]
    num_dict = {'numbers' : num_list, 'name' : 'Numbers'}
    #returns {'output' : {'numbers' : [1,2,3,4,5], 'name' : 'Numbers'}}
    return jsonify({'output' : num_dict})

7. Access Request Data

request.args[‘name’] #get data from query string arguments
request.form[‘name’] #get data form
request.method #request type
request.cookies.get(‘cookie_name’) #cookies
request.files[‘name’] #files

8. Redirects

from flask import url_for, redirect
 
@app.route('/home')
def index():
    return render_template('home.html') 
@app.route('/redirect')
def redirect_example():
    return redirect(url_for('index')) #sends user to /home

9. Abort

from flask import abort()
@app.route(‘/’)
def index():
    abort(404) #returns 404 error
    render_template(‘index.html’) #this never gets executed
    
10. Set Cookie

from flask import make_response
@app.route('/')
def index():
    res = make_response(render_template('index.html'))
    res.set_cookie('cookie_name', 'cookie_value')
    return res

11. Session Handling

import session
app.config['SECRET_KEY'] = 'any secure random string' #must be set to use sessions.

#set session

@app.route('/login_success')
def login_success():
    session['key_name'] = 'key_value' #stores a secure cookie in the browser.
    return redirect(url_for('index'))
#read session
@app.route('/')
def index():
    if 'key_name' in session: #session exists and has key
        session_var = session['key_value']
    else: #session does not exist
""")

sixdaywar = inspect.cleandoc("""
The Six-Day War of 1967 was a brief but pivotal conflict that profoundly shaped the Middle East for decades. It resulted in a decisive Israeli victory and altered the regional power dynamics, with profound consequences that continue to reverberate today. This war, fought between Israel on one side and Egypt, Jordan, and Syria on the other, had its origins in long-standing Arab–Israeli tensions and erupted over the sovereignty of the Holy City of Jerusalem.

The war's roots can be traced back to the 1948 Arab–Israeli War, which resulted in Israel's independence and left underlying tensions and territorial disputes. The flashpoint that triggered the 1967 conflict was the decision by Egyptian President Gamal Abdel Nasser to deploy his troops in the Sinai Peninsula and expel the United Nations Emergency Force (UNEF) stationed there. This move, along with the closure of the Straits of Tiran to Israeli shipping, was a significant concern for Israel's security.

Israel launched a preemptive strike, code-named Operation Focus, on June 5, 1967, catching Egyptian forces off guard and destroying a large portion of their airpower. This surprise attack was a turning point, ensuring Israeli air superiority and setting the stage for a ground offensive. Egypt's defeat was swift, with Israel capturing the Sinai Peninsula in just four days.

Simultaneously, Jordan joined the war, attacking Israeli positions in Jerusalem. Israel responded decisively, and fierce fighting ensued for control of the city. The Jordanian forces were ultimately overwhelmed, leading to Israel's occupation of the West Bank.

Syria also entered the conflict on the side of Egypt, shelling northern Israel. However, Israel launched a successful offensive against Syria, resulting in the capture of the Golan Heights by the end of the war.

The Six-Day War concluded on June 10, 1967, with Israel in control of the Sinai Peninsula, the Gaza Strip, the West Bank, and the Golan Heights. The conflict resulted in a significant shift in the regional power dynamics. Israel's decisive victory demonstrated its military might and altered its standing in the Middle East. The war also led to a wave of nationalist and religious fervor within Israel and had a profound impact on the country's society and culture.

On the other hand, the Arab states suffered a devastating defeat, triggering a wave of soul-searching and recriminations. The war's aftermath fueled resentment and continued tensions, setting the stage for future conflicts. The displacement of hundreds of thousands of Arabs from the captured territories exacerbated the humanitarian crisis and contributed to the ongoing Israeli–Palestinian conflict.

The Six-Day War's consequences extended beyond the immediate regional effects. The war's outcome influenced global powers' relationships and strategies in the Middle East. It heightened Cold War tensions, with the United States and Soviet Union taking different sides and reinforcing their respective allies.

The conflict also impacted the perception of military strategy and the role of air power in particular. Israel's successful preemptive strike and swift ground operations demonstrated the importance of air superiority and the potential for swift, decisive victories. Military strategists worldwide took note of the Israeli approach and its innovative use of combined arms and intelligence.

In the years following the war, Israel consolidated its hold on the captured territories, establishing settlements, and altering the demographic makeup of these areas. The occupation and the subsequent resistance to it have been a significant obstacle to peace and stability in the region. The war's legacy continues to influence Israeli–Palestinian relations, shaping the ongoing quest for a durable solution to the conflict.

The Six-Day War, despite its short duration, had far-reaching consequences, shaping the Middle East's political, social, and strategic landscape for years to come. Its memory remains a significant part of the regional narrative, influencing the perspectives of Israelis, Palestinians, and the broader Arab world. The war's fiftieth anniversary in 2017 prompted reflections on its impact and the ongoing challenges it poses to achieving a comprehensive and sustainable peace in the region.
""")

# cur_sentence = f"\n\nHuman: Please read this: {sixdaywar}\n---\nCreate a timeline.<|endofprompt|>\n\nAssistant: "

cur_sentence = f"\n\nHuman: Write a small website about an AI apocalypse. Show HTML.<|endofprompt|>\n\nAssistant: "

response = generate(
    model,
    tokenizer,
    f"{cur_sentence}",
    max_length=4000,
    freq_penalty=0.2,
    pres_penalty=0.2,
    temperature=0.65,
    top_k=90,
    top_p=1.00,
    min_p=0.05,
    greedy=False,
    token_callback=lambda t: print(t, end='')
)


I am sorry, but as an AI language model, I do not have the capability to create websites. However, I can provide you with the content that you can use to create a website about an AI apocalypse.

Here is the HTML code for a small website about an AI apocalypse:

HTML:
```html
<!DOCTYPE html>
<html>
<head>
    <title>AI apocalypse</title>
    <style>
        body {
            font-family: Arial, sans-serif;
            text-align: center;
            font-family: Arial, sans-serif;
            background-color: #f5f5f5;
        }
    </style>
</head>
<body>

<h1>AI apocalypse</h1>
    <h2>AI apocalypse</h2>
    <p>Once upon a time in a far-off world, there was a group of survivors who had been living in fear for months. They had been on their way to the brink of extinction.</p>
</body>

<h2>JavaScript Code</h2>

<p>Once upon a time, there was a group of survivors who had been living in fear for months. They had been on their way to the brink of extinction.</p>

<p>As they worked togeth

In [ ]:
import json
print(json.dumps(sixdaywar))

In [ ]:
from IPython.core.display import display, HTML
display(HTML(response))